In [1]:
import pandas as pd
import numpy as np

pd.options.display.max_columns = 1000
pd.options.display.max_rows = 1000

In [2]:
train_data = pd.read_csv('../input/gamma-ray-identification/train_processed.csv')
test_data = pd.read_csv('../input/gamma-ray-identification/test_processed.csv')
submission_data = pd.read_csv('../input/gamma-ray-identification/CAX_LogFacies_Submission_File.csv')


In [3]:
train_data['GR_rate'] = train_data.groupby(['well_id'])['GR'].shift(1)
train_data.GR_rate = (train_data.GR - train_data.GR_rate).fillna(0)
train_data.GR_rate = train_data.GR_rate/train_data.GR

In [4]:
test_data['GR_rate'] = test_data.groupby(['well_id'])['GR'].shift(1)
test_data.GR_rate = (test_data.GR - test_data.GR_rate).fillna(0)
test_data.GR_rate = test_data.GR_rate/test_data.GR

In [5]:
train_data.head(5)

row_id  well_id          GR  label  processed_GR  processed_GR2   GR_rate
0       0        0  143.510000      0      0.816197       1.042664  0.000000
1       1        0  112.790928      0      0.609702       0.066697 -0.272354
2       2        0  123.531856      0      0.681903       0.407944  0.086949
3       3        0  111.692784      0      0.602320       0.031808 -0.105997
4       4        0  123.613712      0      0.682453       0.410545  0.096437

In [6]:
test_data.head(5)

unique_id  row_id  well_id          GR  processed_GR  processed_GR2  \
0     CAX_0       0     5000  113.950000      0.599852      -0.297544   
1     CAX_1       1     5000  120.896397      0.641880      -0.092392   
2     CAX_2       2     5000  115.342793      0.608279      -0.256410   
3     CAX_3       3     5000  118.859190      0.629554      -0.152558   
4     CAX_4       4     5000  127.735587      0.683260       0.109593   

    GR_rate  
0  0.000000  
1  0.057457  
2 -0.048149  
3  0.029585  
4  0.069490

In [7]:
submission_data.head(5)

unique_id  label
0     CAX_0    NaN
1     CAX_1    NaN
2     CAX_2    NaN
3     CAX_3    NaN
4     CAX_4    NaN

In [8]:
#!pip install keras_self_attention

In [9]:
from keras.models import Sequential, Model
from keras.layers import TimeDistributed, Dense, Embedding, LSTM, SpatialDropout1D, Input, InputLayer, Bidirectional, Conv1D, Conv2D, MaxPooling1D, MaxPooling2D
from sklearn.model_selection import train_test_split
from keras.utils.np_utils import to_categorical
from keras.models import load_model
from keras_self_attention import SeqSelfAttention
from keras import optimizers

Using TensorFlow backend.


In [10]:
max_len = 110 #train_data[train_data.well_id == 0].shape[0]
n_output = train_data.label.nunique()
num_train_well = train_data.well_id.nunique()
num_test_well = test_data.well_id.nunique()

print (max_len, n_output)

110 5


In [11]:
import tensorflow as tf
import keras.backend as K

def f1(y_true, y_pred):
    y_pred = K.round(y_pred)
    tp = K.sum(K.cast(y_true*y_pred, 'float'), axis=0)
    # tn = K.sum(K.cast((1-y_true)*(1-y_pred), 'float'), axis=0)
    fp = K.sum(K.cast((1-y_true)*y_pred, 'float'), axis=0)
    fn = K.sum(K.cast(y_true*(1-y_pred), 'float'), axis=0)

    p = tp / (tp + fp + K.epsilon())
    r = tp / (tp + fn + K.epsilon())

    f1 = 2*p*r / (p+r+K.epsilon())
    #f1 = tf.where(tf.is_nan(f1), tf.zeros_like(f1), f1)
    return K.mean(f1)

In [12]:
def get_simple_model():
    model = Sequential()
    model.add(InputLayer(input_shape=(max_len,1)))
    model.add(Conv1D(50,20,padding='same',activation='linear',strides=1))
    model.add(Bidirectional(LSTM(100, dropout=0.2, recurrent_dropout=0.2, return_sequences = True)))
    #model.add(SeqSelfAttention(attention_width=50,attention_activation='sigmoid',name='Attention'))
    model.add(TimeDistributed(Dense(n_output,activation='softmax')))
    model.compile(loss = 'categorical_crossentropy', optimizer="adam",metrics = ['accuracy'])
    #print(model.summary())
    return model

In [13]:
def get_simple_cnn_model():
    model = Sequential()
    model.add(InputLayer(input_shape=(max_len,1)))
    model.add(Conv1D(50,20,padding='same',activation='linear',strides=1))
    model.add(Bidirectional(LSTM(100, dropout=0.2, recurrent_dropout=0.2, return_sequences = True)))
    #model.add(SeqSelfAttention(attention_width=None,attention_activation='sigmoid',name='Attention'))
    model.add(TimeDistributed(Dense(n_output,activation='softmax')))
    model.compile(loss = 'categorical_crossentropy', optimizer="adam",metrics = ['accuracy'])
    #print(model.summary())
    return model

In [14]:
def get_model():
    model = Sequential()
    model.add(InputLayer(input_shape=(max_len,1)))
    model.add(Conv1D(50,20,padding='same',activation='linear',strides=1))
    #model.add(Bidirectional(LSTM(200, dropout=0.2, recurrent_dropout=0.2, return_sequences = True)))
    model.add(Bidirectional(LSTM(100, dropout=0.2, recurrent_dropout=0.2, return_sequences = True)))
    model.add(Conv1D(50,20,padding='same',activation='linear',strides=1))
    model.add(Bidirectional(LSTM(50, dropout=0.2, recurrent_dropout=0.2, return_sequences = True)))
    model.add(SeqSelfAttention(attention_width=50,attention_activation='sigmoid',name='Attention'))
    model.add(Dense(n_output,activation='softmax'))
    model.compile(loss = 'categorical_crossentropy', optimizer="adam",metrics = ['accuracy'])
    #print(model.summary())
    return model

In [15]:
model = get_simple_model()
model.summary()

Instructions for updating:
Colocations handled automatically by placer.
Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv1d_1 (Conv1D)            (None, 1100, 50)          1050      
_________________________________________________________________
bidirectional_1 (Bidirection (None, 1100, 200)         120800    
_________________________________________________________________
time_distributed_1 (TimeDist (None, 1100, 5)           1005      
Total params: 122,855
Trainable params: 122,855
Non-trainable params: 0
_________________________________________________________________


In [15]:
from sklearn.model_selection import GroupKFold, KFold
from keras.callbacks import EarlyStopping, ModelCheckpoint, ReduceLROnPlateau 

In [17]:
X = train_data.GR_rate.values.reshape(num_train_well*10,max_len,1)
y = pd.get_dummies(train_data.label).values.reshape(num_train_well*10,max_len,n_output)

In [18]:
y[0]

array([[1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0, 0, 0],
       [1, 0, 0,

In [19]:
batch_size = 32
n_epochs = 50

In [20]:
iter = 0
all_history = {}

for train_index, test_index in KFold(n_splits=5).split(X,y):
    iter += 1
    
    print ("Iteration {}".format(iter))
    
    train_x = X[train_index]
    train_y = y[train_index]
    val_x = X[test_index]
    val_y = y[test_index]
    
    #print (train_x.shape, train_y.shape, val_x.shape, val_y.shape)
    model = get_simple_model()
    #model.load_weights("weights1.hdf5")
    early = EarlyStopping(monitor='val_accuracy', min_delta=0, patience=10, verbose=0, mode='max', baseline=None, restore_best_weights=False)
    lr = ReduceLROnPlateau(monitor='val_loss', factor=0.1, patience=5, verbose=0, mode='auto', min_delta=0.0001, cooldown=0, min_lr=0.000001)
    checkpointer = ModelCheckpoint(monitor='val_accuracy',filepath='../working/weights_simple_lstm_{}.hdf5'.format(iter), mode='max',verbose=1, save_best_only=True)
    
    history = model.fit(train_x, train_y, epochs = n_epochs, batch_size=batch_size, verbose = 1, validation_data=(val_x,val_y), callbacks=[early,lr,checkpointer])
    all_history[iter] = history
    
    break

Iteration 1
Train on 3200 samples, validate on 800 samples
Epoch 1/20
3200/3200 [==============================] - 105s 33ms/step - loss: 0.8758 - acc: 0.6813 - val_loss: 0.7258 - val_acc: 0.7533
Epoch 2/20
3200/3200 [==============================] - 105s 33ms/step - loss: 0.8124 - acc: 0.7121 - val_loss: 0.6343 - val_acc: 0.7779
Epoch 3/20
3200/3200 [==============================] - 105s 33ms/step - loss: 0.7281 - acc: 0.7482 - val_loss: 0.5169 - val_acc: 0.8210
Epoch 4/20
3200/3200 [==============================] - 105s 33ms/step - loss: 0.6437 - acc: 0.7807 - val_loss: 0.4584 - val_acc: 0.8377
Epoch 5/20
3200/3200 [==============================] - 105s 33ms/step - loss: 0.5785 - acc: 0.8038 - val_loss: 0.4304 - val_acc: 0.8526
Epoch 6/20
3200/3200 [==============================] - 105s 33ms/step - loss: 0.5470 - acc: 0.8159 - val_loss: 0.3558 - val_acc: 0.8739
Epoch 7/20
3200/3200 [==============================] - 105s 33ms/step - loss: 0.5193 - acc: 0.8243 - val_loss: 0.3246 

In [22]:
model.save_weights('../working/weights_simple_lstm_1.hdf5')

In [20]:
model = get_simple_cnn_model()
model.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv1d_2 (Conv1D)            (None, 1100, 50)          1050      
_________________________________________________________________
bidirectional_2 (Bidirection (None, 1100, 200)         120800    
_________________________________________________________________
time_distributed_2 (TimeDist (None, 1100, 5)           1005      
Total params: 122,855
Trainable params: 122,855
Non-trainable params: 0
_________________________________________________________________


In [32]:
iter = 0
n_epochs = 20
all_history = {}

for train_index, test_index in KFold(n_splits=5).split(X,y):
    iter += 1
    
    print ("Iteration {}".format(iter))
    
    train_x = X[train_index]
    train_y = y[train_index]
    val_x = X[test_index]
    val_y = y[test_index]
    
    #print (train_x.shape, train_y.shape, val_x.shape, val_y.shape)
    model = get_simple_cnn_model()
    #model.load_weights("weights1.hdf5")
    early = EarlyStopping(monitor='val_acc', min_delta=0, patience=10, verbose=0, mode='max', baseline=None, restore_best_weights=False)
    lr = ReduceLROnPlateau(monitor='val_loss', factor=0.1, patience=5, verbose=0, mode='auto', min_delta=0.0001, cooldown=0, min_lr=0.000001)
    checkpointer = ModelCheckpoint(monitor='val_acc',filepath='../working/weights_simple_lstm_cnn_{}.hdf5'.format(iter), mode='max',verbose=1, save_best_only=True)
    
    history = model.fit(train_x, train_y, epochs = n_epochs, batch_size=batch_size, verbose = 1, validation_data=(val_x,val_y), callbacks=[early,lr,checkpointer])
    all_history[iter] = history
    
    break

Iteration 1
Train on 3200 samples, validate on 800 samples
Epoch 1/20
3200/3200 [==============================] - 127s 40ms/step - loss: 0.2257 - acc: 0.9204 - val_loss: 0.1901 - val_acc: 0.9335

Epoch 00001: val_acc improved from -inf to 0.93348, saving model to ../working/weights_simple_lstm_cnn_1.hdf5
Epoch 2/20
3200/3200 [==============================] - 126s 39ms/step - loss: 0.2101 - acc: 0.9259 - val_loss: 0.1817 - val_acc: 0.9359

Epoch 00002: val_acc improved from 0.93348 to 0.93588, saving model to ../working/weights_simple_lstm_cnn_1.hdf5
Epoch 3/20
3200/3200 [==============================] - 126s 39ms/step - loss: 0.2009 - acc: 0.9290 - val_loss: 0.1754 - val_acc: 0.9381

Epoch 00003: val_acc improved from 0.93588 to 0.93815, saving model to ../working/weights_simple_lstm_cnn_1.hdf5
Epoch 4/20
3200/3200 [==============================] - 126s 39ms/step - loss: 0.1922 - acc: 0.9322 - val_loss: 0.1732 - val_acc: 0.9387

Epoch 00004: val_acc improved from 0.93815 to 0.93873

In [22]:
from keras.layers import Concatenate, BatchNormalization

In [20]:
def get_deep_cnn_model():
    input = Input((max_len,2))
    cnn1 = Conv1D(50,10,padding='same',activation='linear',strides=1)(input)
    cnn2 = Conv1D(50,50,padding='same',activation='linear',strides=1)(input)
    cnn3 = Conv1D(50,100,padding='same',activation='linear',strides=1)(input)
    out = Bidirectional(LSTM(100, dropout=0.2, recurrent_dropout=0.2, return_sequences = True, stateful=True))(Concatenate(axis=-1)([cnn1,cnn2,cnn3]))
    out = TimeDistributed(Dense(n_output,activation='softmax'))(out)
    model = Model(input,out)
    model.compile(loss = 'categorical_crossentropy', optimizer="nadam",metrics = ['accuracy',f1])
    #print(model.summary())
    return model

In [21]:
model = get_deep_cnn_model()
model.summary()

Instructions for updating:
Colocations handled automatically by placer.


NameError: name 'Concatenate' is not defined

In [37]:
iter = 0
n_epochs = 25
all_history = {}

for train_index, test_index in KFold(n_splits=5).split(X,y):
    iter += 1
    
    print ("Iteration {}".format(iter))
    
    train_x = X[train_index]
    train_y = y[train_index]
    val_x = X[test_index]
    val_y = y[test_index]
    
    #print (train_x.shape, train_y.shape, val_x.shape, val_y.shape)
    model = get_deep_cnn_model()
    #model.load_weights("weights1.hdf5")
    early = EarlyStopping(monitor='val_acc', min_delta=0, patience=10, verbose=0, mode='max', baseline=None, restore_best_weights=False)
    lr = ReduceLROnPlateau(monitor='val_loss', factor=0.1, patience=5, verbose=0, mode='auto', min_delta=0.0001, cooldown=0, min_lr=0.000001)
    checkpointer = ModelCheckpoint(monitor='val_acc',filepath='../working/weights_simple_lstm_deep_cnn_{}.hdf5'.format(iter), mode='max',verbose=1, save_best_only=True)
    
    history = model.fit(train_x, train_y, epochs = n_epochs, batch_size=batch_size, verbose = 1, validation_data=(val_x,val_y), callbacks=[early,lr,checkpointer])
    all_history[iter] = history
    
    break

Iteration 1
Train on 3200 samples, validate on 800 samples
Epoch 1/25
3200/3200 [==============================] - 152s 48ms/step - loss: 1.0646 - acc: 0.6037 - val_loss: 0.8085 - val_acc: 0.6861

Epoch 00001: val_acc improved from -inf to 0.68608, saving model to ../working/weights_simple_lstm_deep_cnn_1.hdf5
Epoch 2/25
3200/3200 [==============================] - 148s 46ms/step - loss: 0.6387 - acc: 0.7608 - val_loss: 0.4681 - val_acc: 0.8322

Epoch 00002: val_acc improved from 0.68608 to 0.83221, saving model to ../working/weights_simple_lstm_deep_cnn_1.hdf5
Epoch 3/25
3200/3200 [==============================] - 149s 46ms/step - loss: 0.4207 - acc: 0.8498 - val_loss: 0.3385 - val_acc: 0.8806

Epoch 00003: val_acc improved from 0.83221 to 0.88063, saving model to ../working/weights_simple_lstm_deep_cnn_1.hdf5
Epoch 4/25
3200/3200 [==============================] - 148s 46ms/step - loss: 0.3289 - acc: 0.8838 - val_loss: 0.2791 - val_acc: 0.9027

Epoch 00004: val_acc improved from 0.8

In [24]:
def get_deep_cnn_lstm_cnn_model():
    input = Input((max_len,1))
    cnn1 = Conv1D(50,10,padding='same',activation='linear',strides=1)(input)
    cnn2 = Conv1D(50,50,padding='same',activation='linear',strides=1)(input)
    cnn3 = Conv1D(50,100,padding='same',activation='linear',strides=1)(input)
    out = Bidirectional(LSTM(100, dropout=0.2, recurrent_dropout=0.2, return_sequences = True))(Concatenate(axis=-1)([cnn1,cnn2,cnn3]))
    out = Bidirectional(LSTM(100, dropout=0.2, recurrent_dropout=0.2, return_sequences = True))(out)
    cnn4 = Conv1D(50,10,padding='same',activation='linear',strides=1)(out)
    cnn5 = Conv1D(50,50,padding='same',activation='linear',strides=1)(out)
    cnn6 = Conv1D(50,100,padding='same',activation='linear',strides=1)(out)
    out = Bidirectional(LSTM(100, dropout=0.2, recurrent_dropout=0.2, return_sequences = True))(Concatenate(axis=-1)([cnn4,cnn5,cnn6]))
    out = TimeDistributed(Dense(n_output,activation='softmax'))(out)
    model = Model(input,out)
    model.compile(loss = 'categorical_crossentropy', optimizer="adam",metrics = ['accuracy'])
    #print(model.summary())
    return model

In [25]:
model = get_deep_cnn_lstm_cnn_model()
model.summary()

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_4 (InputLayer)            (None, 1100, 1)      0                                            
__________________________________________________________________________________________________
conv1d_6 (Conv1D)               (None, 1100, 50)     550         input_4[0][0]                    
__________________________________________________________________________________________________
conv1d_7 (Conv1D)               (None, 1100, 50)     2550        input_4[0][0]                    
__________________________________________________________________________________________________
conv1d_8 (Conv1D)               (None, 1100, 50)     5050        input_4[0][0]                    
__________________________________________________________________________________________________
concatenat

In [45]:
iter = 0
n_epochs = 25
all_history = {}

for train_index, test_index in KFold(n_splits=5).split(X,y):
    iter += 1
    
    print ("Iteration {}".format(iter))
    
    train_x = X[train_index]
    train_y = y[train_index]
    val_x = X[test_index]
    val_y = y[test_index]
    
    #print (train_x.shape, train_y.shape, val_x.shape, val_y.shape)
    model = get_deep_cnn_lstm_cnn_model()
    model.load_weights("../working/weights_simple_lstm_deep_cnn_lstm_1.hdf5")
    early = EarlyStopping(monitor='val_acc', min_delta=0, patience=10, verbose=0, mode='max', baseline=None, restore_best_weights=False)
    lr = ReduceLROnPlateau(monitor='val_loss', factor=0.1, patience=5, verbose=0, mode='auto', min_delta=0.0001, cooldown=0, min_lr=0.000001)
    checkpointer = ModelCheckpoint(monitor='val_acc',filepath='../working/weights_simple_lstm_deep_cnn_lstm_{}.hdf5'.format(iter), mode='max',verbose=1, save_best_only=True)
    
    history = model.fit(train_x, train_y, epochs = n_epochs, batch_size=batch_size, verbose = 1, validation_data=(val_x,val_y), callbacks=[early,lr,checkpointer])
    all_history[iter] = history
    
    break

Iteration 1
Train on 3200 samples, validate on 800 samples
Epoch 1/25
3200/3200 [==============================] - 825s 258ms/step - loss: 0.0949 - acc: 0.9662 - val_loss: 0.1118 - val_acc: 0.9614

Epoch 00001: val_acc improved from -inf to 0.96137, saving model to ../working/weights_simple_lstm_deep_cnn_lstm_1.hdf5
Epoch 2/25
3200/3200 [==============================] - 813s 254ms/step - loss: 0.0919 - acc: 0.9676 - val_loss: 0.1150 - val_acc: 0.9607

Epoch 00002: val_acc did not improve from 0.96137
Epoch 3/25
3200/3200 [==============================] - 813s 254ms/step - loss: 0.0912 - acc: 0.9675 - val_loss: 0.1155 - val_acc: 0.9603

Epoch 00003: val_acc did not improve from 0.96137
Epoch 4/25
3200/3200 [==============================] - 812s 254ms/step - loss: 0.0887 - acc: 0.9687 - val_loss: 0.1133 - val_acc: 0.9616

Epoch 00004: val_acc improved from 0.96137 to 0.96156, saving model to ../working/weights_simple_lstm_deep_cnn_lstm_1.hdf5
Epoch 5/25
3200/3200 [====================

KeyboardInterrupt: 

In [26]:
def get_deep_cnn_model2():
    input = Input((max_len,2))
    cnn1 = Conv1D(50,10,padding='same',activation='linear',strides=1)(input)
    cnn1 = BatchNormalization(axis=-1)(cnn1)
    cnn2 = Conv1D(50,50,padding='same',activation='linear',strides=1)(input)
    cnn2 = BatchNormalization(axis=-1)(cnn2)
    cnn3 = Conv1D(50,100,padding='same',activation='linear',strides=1)(input)
    cnn3 = BatchNormalization(axis=-1)(cnn3)
    out = Bidirectional(LSTM(100, dropout=0.2, recurrent_dropout=0.2, return_sequences = True))(Concatenate(axis=-1)([cnn1,cnn2,cnn3]))
    out = TimeDistributed(Dense(n_output,activation='softmax'))(out)
    model = Model(input,out)
    model.compile(loss = 'categorical_crossentropy', optimizer="nadam",metrics = ['accuracy',f1])
    #print(model.summary())
    return model

In [27]:
model = get_deep_cnn_model2()
model.summary()

Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_3 (InputLayer)            (None, 110, 2)       0                                            
__________________________________________________________________________________________________
conv1d_7 (Conv1D)               (None, 110, 50)      1050        input_3[0][0]                    
__________________________________________________________________________________________________
conv1d_8 (Conv1D)               (None, 110, 50)      5050        input_3[0][0]                    
__________________________________________________________________________________________________
conv1d_9 (Conv1D)               (None, 110, 50)      10050       input_3[0][0]               

In [29]:
iter = 0
n_epochs = 25
all_history = {}

for train_index, test_index in KFold(n_splits=5).split(X,y):
    iter += 1
    
    print ("Iteration {}".format(iter))
    
    train_x = train_data[['processed_GR2','GR_rate']].values.reshape(num_train_well*10,max_len,2)[train_index]
    train_y = y[train_index]
    val_x = train_data[['processed_GR2','GR_rate']].values.reshape(num_train_well*10,max_len,2)[test_index]
    val_y = y[test_index]
    
    print (train_x.shape, train_y.shape, val_x.shape, val_y.shape)
    

Iteration 1
(32000, 110, 2) (32000, 110, 5) (8000, 110, 2) (8000, 110, 5)
Iteration 2
(32000, 110, 2) (32000, 110, 5) (8000, 110, 2) (8000, 110, 5)
Iteration 3
(32000, 110, 2) (32000, 110, 5) (8000, 110, 2) (8000, 110, 5)
Iteration 4
(32000, 110, 2) (32000, 110, 5) (8000, 110, 2) (8000, 110, 5)
Iteration 5
(32000, 110, 2) (32000, 110, 5) (8000, 110, 2) (8000, 110, 5)


In [30]:
model = get_deep_cnn_model2()
#model.load_weights("weights1.hdf5")
early = EarlyStopping(monitor='val_f1', min_delta=0, patience=7, verbose=0, mode='max', baseline=None, restore_best_weights=False)
lr = ReduceLROnPlateau(monitor='val_loss', factor=0.1, patience=5, verbose=0, mode='auto', min_delta=0.0001, cooldown=0, min_lr=0.000001)
checkpointer = ModelCheckpoint(monitor='val_f1',filepath='../working/weights_simple_lstm_deep_cnn2_{}.hdf5'.format(iter), mode='max',verbose=1, save_best_only=True)

history = model.fit(train_x, train_y, epochs = n_epochs, batch_size=batch_size, verbose = 1, validation_data=(val_x,val_y), callbacks=[early,lr,checkpointer])
all_history[iter] = history

Instructions for updating:
Use tf.cast instead.
Train on 32000 samples, validate on 8000 samples
Epoch 1/25
32000/32000 [==============================] - 169s 5ms/step - loss: 0.3246 - acc: 0.8834 - f1: 0.7938 - val_loss: 0.2431 - val_acc: 0.9151 - val_f1: 0.8507

Epoch 00001: val_f1 improved from -inf to 0.85073, saving model to ../working/weights_simple_lstm_deep_cnn2_5.hdf5
Epoch 2/25
32000/32000 [==============================] - 156s 5ms/step - loss: 0.2458 - acc: 0.9132 - f1: 0.8497 - val_loss: 0.2311 - val_acc: 0.9178 - val_f1: 0.8615

Epoch 00002: val_f1 improved from 0.85073 to 0.86149, saving model to ../working/weights_simple_lstm_deep_cnn2_5.hdf5
Epoch 3/25
32000/32000 [==============================] - 159s 5ms/step - loss: 0.2290 - acc: 0.9187 - f1: 0.8585 - val_loss: 0.2252 - val_acc: 0.9203 - val_f1: 0.8614

Epoch 00003: val_f1 did not improve from 0.86149
Epoch 4/25
32000/32000 [==============================] - 159s 5ms/step - loss: 0.2174 - acc: 0.9235 - f1: 0.8663 

In [209]:
iter = 0
n_epochs = 25
all_history = {}

for train_index, test_index in KFold(n_splits=5).split(X,y):
    iter += 1
    
    print ("Iteration {}".format(iter))
    
    train_x = train_data[['GR','GR_rate']].values.reshape(num_train_well,max_len,2)[train_index]
    train_y = y[train_index]
    val_x = train_data[['GR','GR_rate']].values.reshape(num_train_well,max_len,2)[test_index]
    val_y = y[test_index]
    
    #print (train_x.shape, train_y.shape, val_x.shape, val_y.shape)
    model = get_deep_cnn_model2()
    #model.load_weights("weights1.hdf5")
    early = EarlyStopping(monitor='val_acc', min_delta=0, patience=10, verbose=0, mode='max', baseline=None, restore_best_weights=False)
    lr = ReduceLROnPlateau(monitor='val_loss', factor=0.1, patience=5, verbose=0, mode='auto', min_delta=0.0001, cooldown=0, min_lr=0.000001)
    checkpointer = ModelCheckpoint(monitor='val_acc',filepath='../working/weights_simple_lstm_deep_cnn3_{}.hdf5'.format(iter), mode='max',verbose=1, save_best_only=True)
    
    history = model.fit(train_x, train_y, epochs = n_epochs, batch_size=batch_size, verbose = 1, validation_data=(val_x,val_y), callbacks=[early,lr,checkpointer])
    all_history[iter] = history
    
    break

Iteration 1
Train on 3200 samples, validate on 800 samples
Epoch 1/25
3200/3200 [==============================] - 178s 56ms/step - loss: 0.5096 - acc: 0.8132 - val_loss: 3.4030 - val_acc: 0.2243

Epoch 00001: val_acc improved from -inf to 0.22426, saving model to ../working/weights_simple_lstm_deep_cnn3_1.hdf5
Epoch 2/25
3200/3200 [==============================] - 161s 50ms/step - loss: 0.2223 - acc: 0.9217 - val_loss: 2.1479 - val_acc: 0.4361

Epoch 00002: val_acc improved from 0.22426 to 0.43610, saving model to ../working/weights_simple_lstm_deep_cnn3_1.hdf5
Epoch 3/25
3200/3200 [==============================] - 161s 50ms/step - loss: 0.1860 - acc: 0.9343 - val_loss: 0.2679 - val_acc: 0.9058

Epoch 00003: val_acc improved from 0.43610 to 0.90582, saving model to ../working/weights_simple_lstm_deep_cnn3_1.hdf5
Epoch 4/25
3200/3200 [==============================] - 160s 50ms/step - loss: 0.1687 - acc: 0.9404 - val_loss: 0.3360 - val_acc: 0.8732

Epoch 00004: val_acc did not improv

In [28]:
def get_deep_cnn_dense_model2():
    input = Input((max_len,2))
    cnn1 = Conv1D(50,10,padding='same',activation='linear',strides=1)(input)
    cnn1 = BatchNormalization(axis=-1)(cnn1)
    cnn2 = Conv1D(50,50,padding='same',activation='linear',strides=1)(input)
    cnn2 = BatchNormalization(axis=-1)(cnn2)
    cnn3 = Conv1D(50,100,padding='same',activation='linear',strides=1)(input)
    cnn3 = BatchNormalization(axis=-1)(cnn3)
    out = Bidirectional(LSTM(100, dropout=0.2, recurrent_dropout=0.2, return_sequences = True))(Concatenate(axis=-1)([cnn1,cnn2,cnn3]))
    out = TimeDistributed(Dense(50))(out)
    out = TimeDistributed(Dense(n_output,activation='softmax'))(out)
    model = Model(input,out)
    model.compile(loss = 'categorical_crossentropy', optimizer="adam",metrics = ['accuracy'])
    #print(model.summary())
    return model

In [29]:
model = get_deep_cnn_dense_model2()
model.summary()

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_6 (InputLayer)            (None, 1100, 2)      0                                            
__________________________________________________________________________________________________
conv1d_15 (Conv1D)              (None, 1100, 50)     1050        input_6[0][0]                    
__________________________________________________________________________________________________
conv1d_16 (Conv1D)              (None, 1100, 50)     5050        input_6[0][0]                    
__________________________________________________________________________________________________
conv1d_17 (Conv1D)              (None, 1100, 50)     10050       input_6[0][0]                    
__________________________________________________________________________________________________
batch_norm

In [121]:
iter = 0
n_epochs = 50
all_history = {}

for train_index, test_index in KFold(n_splits=5).split(X,y):
    iter += 1
    
    print ("Iteration {}".format(iter))
    
    train_x = train_data[['processed_GR2','GR_rate']].values.reshape(num_train_well,max_len,2)[train_index]
    train_y = y[train_index]
    val_x = train_data[['processed_GR2','GR_rate']].values.reshape(num_train_well,max_len,2)[test_index]
    val_y = y[test_index]
    
    #print (train_x.shape, train_y.shape, val_x.shape, val_y.shape)
    model = get_deep_cnn_dense_model2()
    #model.load_weights("weights1.hdf5")
    early = EarlyStopping(monitor='val_acc', min_delta=0, patience=10, verbose=0, mode='max', baseline=None, restore_best_weights=False)
    lr = ReduceLROnPlateau(monitor='val_loss', factor=0.1, patience=5, verbose=0, mode='auto', min_delta=0.0001, cooldown=0, min_lr=0.000001)
    checkpointer = ModelCheckpoint(monitor='val_acc',filepath='../working/weights_simple_lstm_deep_cnn2_dense_{}.hdf5'.format(iter), mode='max',verbose=1, save_best_only=True)
    
    history = model.fit(train_x, train_y, epochs = n_epochs, batch_size=batch_size, verbose = 1, validation_data=(val_x,val_y), callbacks=[early,lr,checkpointer])
    all_history[iter] = history
    
    break

Iteration 1
Train on 3200 samples, validate on 800 samples
Epoch 1/50
3200/3200 [==============================] - 179s 56ms/step - loss: 0.5216 - acc: 0.8049 - val_loss: 0.2560 - val_acc: 0.9101

Epoch 00001: val_acc improved from -inf to 0.91006, saving model to ../working/weights_simple_lstm_deep_cnn2_dense_1.hdf5
Epoch 2/50
3200/3200 [==============================] - 163s 51ms/step - loss: 0.2429 - acc: 0.9140 - val_loss: 0.2009 - val_acc: 0.9292

Epoch 00002: val_acc improved from 0.91006 to 0.92919, saving model to ../working/weights_simple_lstm_deep_cnn2_dense_1.hdf5
Epoch 3/50
3200/3200 [==============================] - 162s 51ms/step - loss: 0.2012 - acc: 0.9287 - val_loss: 0.1811 - val_acc: 0.9370

Epoch 00003: val_acc improved from 0.92919 to 0.93705, saving model to ../working/weights_simple_lstm_deep_cnn2_dense_1.hdf5
Epoch 4/50
3200/3200 [==============================] - 163s 51ms/step - loss: 0.1806 - acc: 0.9360 - val_loss: 0.1677 - val_acc: 0.9407

Epoch 00004: val_

In [30]:
def get_attn_model2():
    input = Input((max_len,2))
    cnn1 = Conv1D(50,10,padding='same',activation='linear',strides=1)(input)
    cnn1 = BatchNormalization(axis=-1)(cnn1)
    cnn2 = Conv1D(50,50,padding='same',activation='linear',strides=1)(input)
    cnn2 = BatchNormalization(axis=-1)(cnn2)
    cnn3 = Conv1D(50,100,padding='same',activation='linear',strides=1)(input)
    cnn3 = BatchNormalization(axis=-1)(cnn3)
    
    out = Bidirectional(LSTM(100, dropout=0.2, recurrent_dropout=0.2, return_sequences = True))(Concatenate(axis=-1)([cnn1,cnn2,cnn3]))
    
    out = Bidirectional(LSTM(100, dropout=0.2, recurrent_dropout=0.2, return_sequences = True))(out)
    
    cnn4 = Conv1D(50,10,padding='same',activation='linear',strides=1)(out)
    cnn4 = BatchNormalization(axis=-1)(cnn4)
    cnn5 = Conv1D(50,50,padding='same',activation='linear',strides=1)(out)
    cnn5 = BatchNormalization(axis=-1)(cnn5)
    cnn6 = Conv1D(50,100,padding='same',activation='linear',strides=1)(out)
    cnn6 = BatchNormalization(axis=-1)(cnn6)
    
    out = Bidirectional(LSTM(100, dropout=0.2, recurrent_dropout=0.2, return_sequences = True))(Concatenate(axis=-1)([cnn4,cnn5,cnn6]))
    attn = SeqSelfAttention(units=20,attention_width=20,attention_activation='sigmoid',name='Attention1')(out)
    out = TimeDistributed(Dense(n_output,activation='softmax'))(Concatenate(axis=-1)([out,attn]))
    model = Model(input,out)
    model.compile(loss = 'categorical_crossentropy', optimizer="adam",metrics = ['accuracy'])
    #print(model.summary())
    return model

In [31]:
def get_multout_model():
    input = Input((max_len,2))
    cnn1 = Conv1D(50,10,padding='same',activation='linear',strides=1)(input)
    cnn1 = BatchNormalization(axis=-1)(cnn1)
    cnn2 = Conv1D(50,50,padding='same',activation='linear',strides=1)(input)
    cnn2 = BatchNormalization(axis=-1)(cnn2)
    cnn3 = Conv1D(50,100,padding='same',activation='linear',strides=1)(input)
    cnn3 = BatchNormalization(axis=-1)(cnn3)
    out1 = TimeDistributed(Dense(n_output,activation='softmax'))(Concatenate(axis=-1)([cnn1,cnn2,cnn3]))
    
    out = Bidirectional(LSTM(100, dropout=0.2, recurrent_dropout=0.2, return_sequences = True))(Concatenate(axis=-1)([cnn1,cnn2,cnn3]))
    out2 = TimeDistributed(Dense(n_output,activation='softmax'))(out)
    
    out = Bidirectional(LSTM(100, dropout=0.2, recurrent_dropout=0.2, return_sequences = True))(out)
    out3 = TimeDistributed(Dense(n_output,activation='softmax'))(out)
    
    cnn4 = Conv1D(50,10,padding='same',activation='linear',strides=1)(out)
    cnn4 = BatchNormalization(axis=-1)(cnn4)
    cnn5 = Conv1D(50,50,padding='same',activation='linear',strides=1)(out)
    cnn5 = BatchNormalization(axis=-1)(cnn5)
    cnn6 = Conv1D(50,100,padding='same',activation='linear',strides=1)(out)
    cnn6 = BatchNormalization(axis=-1)(cnn6)
    
    out4 = TimeDistributed(Dense(n_output,activation='softmax'))(Concatenate(axis=-1)([cnn4,cnn5,cnn6]))
    
    out = Bidirectional(LSTM(100, dropout=0.2, recurrent_dropout=0.2, return_sequences = True))(Concatenate(axis=-1)([cnn4,cnn5,cnn6]))
    #attn = SeqSelfAttention(units=20,attention_width=20,attention_activation='sigmoid',name='Attention1')(out)
    out = TimeDistributed(Dense(n_output,activation='softmax'))(out)
    model = Model(input,[out1,out2,out3,out4,out])
    model.compile(loss = 'categorical_crossentropy', optimizer="adam",metrics = ['accuracy'])
    #print(model.summary())
    return model

In [32]:
def get_deep_lstm_model():
    input = Input((max_len,2))

    out = LSTM(512, dropout=0.2, recurrent_dropout=0.2, return_sequences = True)(input)
    out = LSTM(256, dropout=0.2, recurrent_dropout=0.2, return_sequences = True)(out)

    cnn4 = Conv1D(100,10,padding='same',strides=1)(out)
    cnn4 = BatchNormalization(axis=-1)(cnn4)
    cnn5 = Conv1D(100,50,padding='same',strides=1)(out)
    cnn5 = BatchNormalization(axis=-1)(cnn5)
    cnn6 = Conv1D(100,100,padding='same',strides=1)(out)
    cnn6 = BatchNormalization(axis=-1)(cnn6)
    
    out = Bidirectional(LSTM(100, dropout=0.2, recurrent_dropout=0.2, return_sequences = True))(Concatenate(axis=-1)([cnn4,cnn5,cnn6,out]))
    out = TimeDistributed(Dense(n_output,activation='softmax'))(out)
    model = Model(input,out)
    model.compile(loss = 'categorical_crossentropy', optimizer="adam",metrics = ['accuracy'])
    #print(model.summary())
    return model

In [33]:
def get_very_deep_lstm_cnn_bn_model():
    input = Input((max_len,2))
    cnn1 = Conv1D(100,10,padding='same',strides=1)(input)
    cnn1 = BatchNormalization(axis=-1)(cnn1)
    cnn2 = Conv1D(100,50,padding='same',strides=1)(input)
    cnn2 = BatchNormalization(axis=-1)(cnn2)
    cnn3 = Conv1D(100,100,padding='same',strides=1)(input)
    cnn3 = BatchNormalization(axis=-1)(cnn3)
    out = Bidirectional(LSTM(256, dropout=0.2, recurrent_dropout=0.2, return_sequences = True))(Concatenate(axis=-1)([cnn1,cnn2,cnn3,input]))
    out = BatchNormalization(axis=-1)(out)
    out = Bidirectional(LSTM(256, dropout=0.2, recurrent_dropout=0.2, return_sequences = True))(out)
    out = BatchNormalization(axis=-1)(out)
    cnn4 = Conv1D(100,10,padding='same',strides=1)(out)
    cnn4 = BatchNormalization(axis=-1)(cnn4)
    cnn5 = Conv1D(100,50,padding='same',strides=1)(out)
    cnn5 = BatchNormalization(axis=-1)(cnn5)
    cnn6 = Conv1D(100,100,padding='same',strides=1)(out)
    cnn6 = BatchNormalization(axis=-1)(cnn6)
    out = Bidirectional(LSTM(100, dropout=0.2, recurrent_dropout=0.2, return_sequences = True))(Concatenate(axis=-1)([cnn4,cnn5,cnn6,out]))
    out = TimeDistributed(Dense(n_output,activation='softmax'))(out)
    model = Model(input,out)
    model.compile(loss = 'categorical_crossentropy', optimizer="adam",metrics = ['accuracy'])
    #print(model.summary())
    return model

In [47]:
def get_very_deep_lstm_cnn_bn_model_with_attn():
    input = Input((max_len,2))
    
    inter_model = get_very_deep_lstm_cnn_bn_model()
    inter_model.load_weights("../models/weights_very_deep_cnn_lstm_bn_1.hdf5")

    cnn1 = inter_model.layers[1](input)
    cnn1 = inter_model.layers[4](cnn1)
    cnn2 = inter_model.layers[2](input)
    cnn2 = inter_model.layers[5](cnn2)
    cnn3 = inter_model.layers[3](input)
    cnn3 = inter_model.layers[6](cnn3)
    out = inter_model.layers[7]([cnn1,cnn2,cnn3,input])
    out = inter_model.layers[8](out)
    out = inter_model.layers[9](out)
    out = inter_model.layers[10](out)
    out = inter_model.layers[11](out)
    cnn4 = inter_model.layers[12](out)
    cnn4 = inter_model.layers[15](cnn4)
    cnn5 = inter_model.layers[13](out)
    cnn5 = inter_model.layers[16](cnn5)
    cnn6 = inter_model.layers[14](out)
    cnn6 = inter_model.layers[17](cnn6)
    out = inter_model.layers[18]([cnn4,cnn5,cnn6,out])
    out = inter_model.layers[19](out)
    
    out = Bidirectional(LSTM(50, dropout=0.2, recurrent_dropout=0.2, return_sequences = True))(out)
    attn = SeqSelfAttention(units=20,attention_width=50,attention_activation='sigmoid',name='Attention1')(out)
    out = TimeDistributed(Dense(n_output,activation='softmax'))(Concatenate(axis=-1)([attn,out]))
    model = Model(input,out)
    
    for layer in model.layers[1:-4]:
        layer.trainable = False
        
    return model

In [35]:
def get_deep_bilstm_model():
    input = Input((max_len,2))

    out = Bidirectional(LSTM(256, dropout=0.2, recurrent_dropout=0.2, return_sequences = True))(input)
    out = Bidirectional(LSTM(128, dropout=0.2, recurrent_dropout=0.2, return_sequences = True))(out)

    cnn4 = Conv1D(100,10,padding='same',strides=1)(out)
    cnn4 = BatchNormalization(axis=-1)(cnn4)
    cnn5 = Conv1D(100,50,padding='same',strides=1)(out)
    cnn5 = BatchNormalization(axis=-1)(cnn5)
    cnn6 = Conv1D(100,100,padding='same',strides=1)(out)
    cnn6 = BatchNormalization(axis=-1)(cnn6)
    
    out = Bidirectional(LSTM(100, dropout=0.2, recurrent_dropout=0.2, return_sequences = True))(Concatenate(axis=-1)([cnn4,cnn5,cnn6,out]))
    out = TimeDistributed(Dense(n_output,activation='softmax'))(out)
    model = Model(input,out)
    model.compile(loss = 'categorical_crossentropy', optimizer="adam",metrics = ['accuracy'])
    #print(model.summary())
    return model

In [37]:
test_model = get_deep_lstm_model()
test_model.load_weights("../models/weights_very_deep_lstm2_cnn_lstm_1.hdf5")

In [43]:
test_model = get_very_deep_lstm_cnn_bn_model()
test_model.load_weights("../models/weights_very_deep_cnn_lstm_bn_1.hdf5")

In [48]:
test_model = get_very_deep_lstm_cnn_bn_model_with_attn()
test_model.load_weights("../models/weights_very_deep_cnn_lstm_bn_attn_1.hdf5")

In [39]:
iter = 0

for train_index, test_index in KFold(n_splits=5).split(X,y):
    iter += 1
    
    print ("Iteration {}".format(iter))
    
    train_x = train_data[['processed_GR2','GR_rate']].values.reshape(num_train_well,max_len,2)[train_index]
    train_y = y[train_index]
    val_x = train_data[['processed_GR2','GR_rate']].values.reshape(num_train_well,max_len,2)[test_index]
    val_y = y[test_index]
    
    break

Iteration 1


In [49]:
test_pred = test_model.predict(val_x).argmax(-1)
test_pred_val = test_pred.reshape(test_pred.shape[0]*test_pred.shape[1])

val_actual = val_y.argmax(-1)
val_actual = val_actual.reshape(val_actual.shape[0]*val_actual.shape[1])

In [41]:
from sklearn.metrics import accuracy_score, f1_score, confusion_matrix

In [50]:
print (accuracy_score(val_actual,test_pred_val))
print (f1_score(val_actual,test_pred_val,average='macro'))
print (confusion_matrix(val_actual,test_pred_val))

0.9666784090909091
0.9540715828730058
[[454840   1332     17   2781   2187]
 [  1737  95986   1364   1648   1403]
 [    12   1617 100164   1137   1250]
 [  2921   2469    914  97842    594]
 [  2773   1433   1152    582 101845]]


In [166]:
print (accuracy_score(val_actual,test_pred_val))
print (f1_score(val_actual,test_pred_val,average='macro'))
conf = confusion_matrix(val_actual,test_pred_val)
print (conf/conf.sum(axis=1)[:,np.newaxis])

0.9666784090909091
0.9540715828730058
[[9.86301845e-01 2.88838725e-03 3.68638013e-05 6.03048420e-03
  4.74241961e-03]
 [1.70064031e-02 9.39767765e-01 1.33544812e-02 1.61350330e-02
  1.37363175e-02]
 [1.15185256e-04 1.55212133e-02 9.61451334e-01 1.09138030e-02
  1.19984642e-02]
 [2.78881039e-02 2.35726561e-02 8.72637006e-03 9.34141684e-01
  5.67118579e-03]
 [2.57271420e-02 1.32949854e-02 1.06879436e-02 5.39963817e-03
  9.44890291e-01]]


In [51]:
val_data = train_data.iloc[:val_x.shape[0]*val_x.shape[1]]
val_data['true_label'] = val_actual
val_data['pred_label'] = test_pred_val

/Users/victor/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
/Users/victor/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  This is separate from the ipykernel package so we can avoid doing imports until


In [52]:
val_data.head(10)

row_id  well_id          GR  label  processed_GR  processed_GR2   GR_rate  \
0       0        0  143.510000      0      0.816197       1.042664  0.000000   
1       1        0  112.790928      0      0.609702       0.066697 -0.272354   
2       2        0  123.531856      0      0.681903       0.407944  0.086949   
3       3        0  111.692784      0      0.602320       0.031808 -0.105997   
4       4        0  123.613712      0      0.682453       0.410545  0.096437   
5       5        0  120.414641      0      0.660949       0.308908 -0.026567   
6       6        0  123.145569      0      0.679306       0.395672  0.022176   
7       7        0  114.216497      0      0.619285       0.111989 -0.078177   
8       8        0  119.387425      0      0.654044       0.276273  0.043312   
9       9        0  132.728353      0      0.743722       0.700124  0.100513   

   true_label  pred_label  
0           0           0  
1           0           0  
2           0           0  
3           0           0  
4           0           0  
5           0           0  
6           0           0  
7           0           0  
8           0           0  
9           0           0

In [53]:
val_accuracy = val_data.groupby(['well_id'])['label','pred_label'].agg(lambda x: accuracy_score(x['label'],x['pred_label'])).reset_index()
val_accuracy.label.describe()

count    800.000000
mean       0.963043
std        0.021290
min        0.870000
25%        0.950909
50%        0.967273
75%        0.979091
max        0.997273
Name: label, dtype: float64

In [54]:
val_accuracy.sort_values(['label'],ascending=[True]).head(10)

well_id     label  pred_label
142      142  0.870000    0.870000
600      600  0.885455    0.885455
385      385  0.886364    0.886364
547      547  0.889091    0.889091
195      195  0.895455    0.895455
146      146  0.896364    0.896364
508      508  0.896364    0.896364
598      598  0.897273    0.897273
461      461  0.900000    0.900000
380      380  0.900909    0.900909

In [59]:
test_pred = test_model.predict(test_data.GR_rate.values.reshape(num_test_well,max_len,1)).argmax(-1)
test_pred = test_pred.reshape(test_pred.shape[0]*test_pred.shape[1])

In [60]:
submission_data.label = test_pred

In [61]:
submission_data.head(10)

unique_id  label
0     CAX_0      3
1     CAX_1      0
2     CAX_2      0
3     CAX_3      0
4     CAX_4      0
5     CAX_5      0
6     CAX_6      0
7     CAX_7      0
8     CAX_8      4
9     CAX_9      4

In [62]:
submission_data.to_csv("../data/submission_model11.csv",index=False)

In [63]:
submission_data_prev_best = pd.read_csv('../data/submission7_cnn_bilstm_attn.csv')

In [64]:
submission_data_prev_best.head(10)

unique_id  label
0     CAX_0      0
1     CAX_1      0
2     CAX_2      0
3     CAX_3      0
4     CAX_4      0
5     CAX_5      0
6     CAX_6      0
7     CAX_7      0
8     CAX_8      0
9     CAX_9      0

In [65]:
submission_data.loc[submission_data.index%1100 == 0,"label"] = submission_data_prev_best.iloc[submission_data_prev_best.index%1100 == 0].label

In [66]:
submission_data.head(10)

unique_id  label
0     CAX_0      0
1     CAX_1      0
2     CAX_2      0
3     CAX_3      0
4     CAX_4      0
5     CAX_5      0
6     CAX_6      0
7     CAX_7      0
8     CAX_8      4
9     CAX_9      4

In [67]:
submission_data.to_csv('../data/submission_model11_ensemble.csv',index=False)

### Ensemble

In [211]:
train_data[['row_id','label']].corr()

row_id     label
row_id  1.000000 -0.048928
label  -0.048928  1.000000

In [212]:
pd.crosstab(train_data.label,train_data.row_id)

row_id  0     1     2     3     4     5     6     7     8     9     10    \
label                                                                      
0       3949  3904  3847  3787  3732  3670  3621  3569  3523  3477  3420   
1          9    19    30    41    56    75    83    92   100   109   128   
2         16    27    40    57    70    91   104   121   138   153   165   
3         14    28    46    62    80    91   106   119   131   142   161   
4         12    22    37    53    62    73    86    99   108   119   126   

row_id  11    12    13    14    15    16    17    18    19    20    21    \
label                                                                      
0       3374  3338  3296  3255  3205  3165  3120  3071  3031  2996  2951   
1        140   145   155   169   178   191   200   216   226   231   243   
2        176   187   192   208   217   224   230   239   254   264   272   
3        169   180   194   201   217   231   247   256   261   267   281   
4        141   150   163   167   183   189   203   218   228   242   253   

row_id  22    23    24    25    26    27    28    29    30    31    32    \
label                                                                      
0       2915  2877  2837  2805  2777  2748  2716  2680  2652  2627  2614   
1        256   260   262   266   275   286   291   299   308   314   315   
2        282   292   304   311   318   318   330   333   340   347   348   
3        287   300   309   323   333   340   354   370   375   379   377   
4        260   271   288   295   297   308   309   318   325   333   346   

row_id  33    34    35    36    37    38    39    40    41    42    43    \
label                                                                      
0       2596  2562  2532  2504  2480  2461  2451  2427  2402  2371  2365   
1        319   320   324   333   338   347   353   360   371   382   379   
2        350   356   368   375   385   383   383   392   400   404   414   
3        377   395   398   405   409   418   424   427   428   433   434   
4        358   367   378   383   388   391   389   394   399   410   408   

row_id  44    45    46    47    48    49    50    51    52    53    54    \
label                                                                      
0       2351  2323  2295  2270  2251  2246  2231  2223  2216  2205  2199   
1        383   385   392   400   406   406   401   400   401   408   412   
2        417   433   445   444   452   449   456   454   457   460   462   
3        438   443   447   455   455   466   477   479   482   480   484   
4        411   416   421   431   436   433   435   444   444   447   443   

row_id  55    56    57    58    59    60    61    62    63    64    65    \
label                                                                      
0       2177  2151  2141  2126  2102  2102  2077  2079  2067  2066  2055   
1        422   434   433   440   450   447   451   452   466   471   466   
2        467   475   478   482   486   496   501   488   481   482   492   
3        487   493   495   497   503   501   514   521   520   523   526   
4        447   447   453   455   459   454   457   460   466   458   461   

row_id  66    67    68    69    70    71    72    73    74    75    76    \
label                                                                      
0       2048  2051  2028  2021  2023  2004  1997  1987  1978  1978  1970   
1        470   474   475   476   479   488   498   502   508   511   510   
2        496   498   508   502   496   498   498   498   504   500   503   
3        521   520   524   536   539   541   535   536   531   529   533   
4        465   457   465   465   463   469   472   477   479   482   484   

row_id  77    78    79    80    81    82    83    84    85    86    87    \
label                                                                      
0       1972  1970  1955  1942  1937  1943  1945  1933  1936  1928  1929   
1        515   526   528   535   532   53

In [51]:
def get_val_output(model,weight_path,val_data,test_data,model_num):
    model.load_weights(weight_path)
    val_pred = model.predict(val_data)
    global val_pred_df, submission_data
    #val_pred_df = train_data.iloc[:val_x.shape[0]*val_x.shape[1]].copy()
    for i in range(val_pred.shape[-1]):
        val_pred_df['pred_{}_{}'.format(model_num,i)] = val_pred[:,:,i].reshape(val_pred.shape[0]*val_pred.shape[1]) 
    val_pred_df['pred_{}'.format(model_num)] = val_pred.argmax(axis=-1).reshape(val_pred.shape[0]*val_pred.shape[1])
    
    test_pred = model.predict(test_data)
    for i in range(test_pred.shape[-1]):
        submission_data['pred_{}_{}'.format(model_num,i)] = test_pred[:,:,i].reshape(test_pred.shape[0]*test_pred.shape[1])
    submission_data['pred_{}'.format(model_num)] = test_pred.argmax(axis=-1).reshape(test_pred.shape[0]*test_pred.shape[1])
        

In [66]:
val_pred_df = train_data.iloc[:val_x.shape[0]*val_x.shape[1]].copy()
submission_data = pd.read_csv('../input/gamma-ray-identification/CAX_LogFacies_Submission_File.csv')

In [53]:
val_x1 = train_data[['GR_rate']].values.reshape(num_train_well,max_len,1)[test_index]
val_x2 = train_data[['processed_GR2','GR_rate']].values.reshape(num_train_well,max_len,2)[test_index]
test_x1 = test_data[['GR_rate']].values.reshape(num_test_well,max_len,1)
test_x2 = test_data[['processed_GR2','GR_rate']].values.reshape(num_test_well,max_len,2)


In [56]:
test_model = get_simple_model()
get_val_output(test_model,'../working/weights_simple_lstm_1.hdf5',val_x1,test_x1,1)

ValueError: You are trying to load a weight file containing 2 layers into a model with 3 layers.

In [67]:
test_model = get_simple_cnn_model()
get_val_output(test_model,'../working/weights_simple_lstm_cnn_1.hdf5',val_x1,test_x1,2)

In [68]:
test_model = get_deep_cnn_model()
get_val_output(test_model,'../working/weights_simple_lstm_deep_cnn_1.hdf5',val_x1,test_x1,3)

In [69]:
test_model = get_deep_cnn_lstm_cnn_model()
get_val_output(test_model,'../working/weights_simple_lstm_deep_cnn_lstm_1_50epochs.hdf5',val_x1,test_x1,4)

In [70]:
test_model = get_deep_cnn_model2()
get_val_output(test_model,'../working/weights_simple_lstm_deep_cnn2_1.hdf5',val_x2,test_x2,5)

In [71]:
test_model = get_attn_model2()
get_val_output(test_model,'../working/weights_deep_cnn_lstm_bn_attention_1_best.hdf5',val_x2,test_x2,6)

In [72]:
test_model = get_multout_model()
test_model.load_weights('../working/weights_deep_cnn_lstm_bn_multout_1.hdf5')

model_num = 7
for out in test_model.predict(val_x2):
    for i in range(5):
        val_pred_df['pred_{}_{}'.format(model_num,i)] = out[:,:,i].reshape(out.shape[0]*out.shape[1])
    val_pred_df['pred_{}'.format(model_num)] = out.argmax(axis=-1).reshape(out.shape[0]*out.shape[1])
    model_num += 1
    
model_num = 7
for out in test_model.predict(test_x2):
    for i in range(5):
        submission_data['pred_{}_{}'.format(model_num,i)] = out[:,:,i].reshape(out.shape[0]*out.shape[1])
    submission_data['pred_{}'.format(model_num)] = out.argmax(axis=-1).reshape(out.shape[0]*out.shape[1])
    model_num += 1

In [73]:
test_model = get_deep_lstm_model()
get_val_output(test_model,'../working/weights_very_deep_lstm2_cnn_lstm_1.hdf5',val_x2,test_x2,12)

In [74]:
test_model = get_very_deep_lstm_cnn_bn_model()
get_val_output(test_model,'../working/weights_very_deep_cnn_lstm_bn_1.hdf5',val_x2,test_x2,13)

In [75]:
test_model = get_very_deep_lstm_cnn_bn_model_with_attn()
get_val_output(test_model,'../working/weights_very_deep_cnn_lstm_bn_attn_1.hdf5',val_x2,test_x2,14)

In [76]:
val_pred_df.columns

Index(['row_id', 'well_id', 'GR', 'label', 'processed_GR', 'processed_GR2',
       'GR_rate', 'pred_2_0', 'pred_2_1', 'pred_2_2', 'pred_2_3', 'pred_2_4',
       'pred_2', 'pred_3_0', 'pred_3_1', 'pred_3_2', 'pred_3_3', 'pred_3_4',
       'pred_3', 'pred_4_0', 'pred_4_1', 'pred_4_2', 'pred_4_3', 'pred_4_4',
       'pred_4', 'pred_5_0', 'pred_5_1', 'pred_5_2', 'pred_5_3', 'pred_5_4',
       'pred_5', 'pred_6_0', 'pred_6_1', 'pred_6_2', 'pred_6_3', 'pred_6_4',
       'pred_6', 'pred_7_0', 'pred_7_1', 'pred_7_2', 'pred_7_3', 'pred_7_4',
       'pred_7', 'pred_8_0', 'pred_8_1', 'pred_8_2', 'pred_8_3', 'pred_8_4',
       'pred_8', 'pred_9_0', 'pred_9_1', 'pred_9_2', 'pred_9_3', 'pred_9_4',
       'pred_9', 'pred_10_0', 'pred_10_1', 'pred_10_2', 'pred_10_3',
       'pred_10_4', 'pred_10', 'pred_11_0', 'pred_11_1', 'pred_11_2',
       'pred_11_3', 'pred_11_4', 'pred_11', 'pred_12_0', 'pred_12_1',
       'pred_12_2', 'pred_12_3', 'pred_12_4', 'pred_12', 'pred_13_0',
       'pred_13_1', 'pred_13

In [98]:
val_pred_df.to_csv('../data/ensemble_valdata_new.csv',index=False)
submission_data.to_csv('../data/ensemble_testdata_new.csv',index=False)

In [77]:
val_pred_df[val_pred_df.label != val_pred_df.pred_4][['row_id','well_id','label','pred_2','pred_3','pred_4','pred_5','pred_6', 'pred_7', 'pred_8','pred_9','pred_10','pred_11','pred_12','pred_13','pred_14']].head(50)

row_id  well_id  label  pred_2  pred_3  pred_4  pred_5  pred_6  pred_7  \
315      315        0      1       0       0       0       0       0       0   
361      361        0      1       0       0       0       1       0       0   
362      362        0      1       0       0       0       1       0       0   
363      363        0      1       0       0       0       0       0       0   
460      460        0      3       0       0       0       3       3       0   
461      461        0      3       0       0       0       0       3       0   
593      593        0      4       2       2       2       2       2       1   
594      594        0      4       2       2       2       2       2       2   
595      595        0      4       2       2       2       2       2       2   
596      596        0      4       2       2       2       2       2       2   
597      597        0      4       2       2       2       2       2       2   
598      598        0      4       2       2       2       2       2       2   
599      599        0      4       2       2       2       2       2       2   
869      869        0      0       1       1       1       1       1       0   
870      870        0      0       1       1       1       1       0       0   
910      910        0      4       0       0       0       0       0       0   
985      985        0      3       4       4       4       4       4       3   
986      986        0      3       4       4       4       4       4       3   
987      987        0      3       4       4       4       4       4       3   
988      988        0      3       4       4       4       4       4       3   
989      989        0      3       4       4       4       4       4       3   
990      990        0      3       3       3       4       3       3       3   
992      992        0      3       3       3       1       3       3       3   
993      993        0      3       3       3       1       3       3       0   
1007    1007        0      3       0       3       0       0       0       0   
1008    1008        0      3       0       3       0       0       0       0   
1009    1009        0      3       0       0       0       0       0       0   
1383     283        1      1       0       4       0       0       0       0   
1384     284        1      1       4       4       0       0       0       0   
1385     285        1      1       4       4       0       0       1       0   
1456     356        1      3       3       3       1       1       3       0   
1457     357        1      3       3       3       1       1       3       0   
1458     358        1      3       3       3       1       1       3       0   
1459     359        1      3       0       3       1       1       3       0   
1460     360        1      3       0       3       1       1       0       0   
1461     361        1      3       0       3       1       0       0       0   
1464     364        1      3       0       0       1       0       0       0   
1465     365        1      3       0       0       1       0       0       0   
1466     366        1      3       0       0       1       0       0       0   
1467     367        1      3       0       0       1       0       0       0   
1468     368        1      3       0       0       1       0       0       0   
1469     369        1      3       0       0       1       0       0       0   
1470     370        1      3       0       0       1       0       0       0   
1570     470        1      4       3       3       3       4       4       2   
1647     547        1      0       3       3       3       3       3       0   
1648     548        1      0       0       3       3       3       3       0   
2707     507        2      2       3       3       3       3       2       4   
2710     510        2      2       3       3       3       3       1       4   
2711     511        2      2       3       3       3       3       1       4   
2774  

In [78]:
val_pred_df[['label','pred_2','pred_3','pred_4','pred_5','pred_6', 'pred_7', 'pred_8','pred_9','pred_10','pred_11','pred_12','pred_13','pred_14']].corr()

label    pred_2    pred_3    pred_4    pred_5    pred_6    pred_7  \
label    1.000000  0.926059  0.927152  0.943949  0.937754  0.934296  0.517419   
pred_2   0.926059  1.000000  0.964522  0.947887  0.950083  0.943498  0.528181   
pred_3   0.927152  0.964522  1.000000  0.950516  0.951223  0.945781  0.523588   
pred_4   0.943949  0.947887  0.950516  1.000000  0.958393  0.954035  0.518793   
pred_5   0.937754  0.950083  0.951223  0.958393  1.000000  0.958877  0.523711   
pred_6   0.934296  0.943498  0.945781  0.954035  0.958877  1.000000  0.515474   
pred_7   0.517419  0.528181  0.523588  0.518793  0.523711  0.515474  1.000000   
pred_8   0.909493  0.928123  0.932102  0.928089  0.937807  0.939842  0.512569   
pred_9   0.913888  0.928178  0.930950  0.933038  0.941431  0.950413  0.502633   
pred_10  0.922529  0.934350  0.937051  0.941520  0.947379  0.958179  0.508089   
pred_11  0.922876  0.934784  0.936982  0.942169  0.947883  0.959545  0.507558   
pred_12  0.941711  0.942213  0.945238  0.960525  0.957702  0.953299  0.518796   
pred_13  0.950285  0.941148  0.943595  0.962703  0.957659  0.954806  0.518447   
pred_14  0.950006  0.940763  0.943042  0.961837  0.957214  0.954995  0.517990   

           pred_8    pred_9   pred_10   pred_11   pred_12   pred_13   pred_14  
label    0.909493  0.913888  0.922529  0.922876  0.941711  0.950285  0.950006  
pred_2   0.928123  0.928178  0.934350  0.934784  0.942213  0.941148  0.940763  
pred_3   0.932102  0.930950  0.937051  0.936982  0.945238  0.943595  0.943042  
pred_4   0.928089  0.933038  0.941520  0.942169  0.960525  0.962703  0.961837  
pred_5   0.937807  0.941431  0.947379  0.947883  0.957702  0.957659  0.957214  
pred_6   0.939842  0.950413  0.958179  0.959545  0.953299  0.954806  0.954995  
pred_7   0.512569  0.502633  0.508089  0.507558  0.518796  0.518447  0.517990  
pred_8   1.000000  0.952419  0.946973  0.945378  0.928515  0.923442  0.923082  
pred_9   0.952419  1.000000  0.975276  0.973969  0.933187  0.930740  0.931131  
pred_10  0.946973  0.975276  1.000000  0.985227  0.941624  0.940625  0.941041  
pred_11  0.945378  0.973969  0.985227  1.000000  0.941979  0.941337  0.941737  
pred_12  0.928515  0.933187  0.941624  0.941979  1.000000  0.958595  0.958342  
pred_13  0.923442  0.930740  0.940625  0.941337  0.958595  1.000000  0.991640  
pred_14  0.923082  0.931131  0.941041  0.941737  0.958342  0.991640  1.000000

In [79]:
val_pred_df[val_pred_df.label != val_pred_df.pred_12][val_pred_df.label != val_pred_df.pred_13][val_pred_df.label != val_pred_df.pred_14][val_pred_df.label != val_pred_df.pred_2][val_pred_df.label != val_pred_df.pred_3][val_pred_df.label != val_pred_df.pred_4][val_pred_df.label != val_pred_df.pred_5][val_pred_df.label != val_pred_df.pred_6][val_pred_df.label != val_pred_df.pred_7][val_pred_df.label != val_pred_df.pred_8][val_pred_df.label != val_pred_df.pred_9][val_pred_df.label != val_pred_df.pred_10][val_pred_df.label != val_pred_df.pred_11].label.value_counts()

/Users/victor/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  """Entry point for launching an IPython kernel.


3    2652
4    2479
1    2181
2     762
0     157
Name: label, dtype: int64

In [80]:
1 - val_pred_df[val_pred_df.label != val_pred_df.pred_12][val_pred_df.label != val_pred_df.pred_13][val_pred_df.label != val_pred_df.pred_14][val_pred_df.label != val_pred_df.pred_2][val_pred_df.label != val_pred_df.pred_3][val_pred_df.label != val_pred_df.pred_4][val_pred_df.label != val_pred_df.pred_5][val_pred_df.label != val_pred_df.pred_6][val_pred_df.label != val_pred_df.pred_7][val_pred_df.label != val_pred_df.pred_8][val_pred_df.label != val_pred_df.pred_9][val_pred_df.label != val_pred_df.pred_10][val_pred_df.label != val_pred_df.pred_11].label.value_counts().shape[0]*1.0/val_pred_df.shape[0]

/Users/victor/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  """Entry point for launching an IPython kernel.


0.9999943181818182

In [95]:
submission_data['processed_GR'] = test_data.processed_GR
submission_data['processed_GR2'] = test_data.processed_GR2
submission_data['GR_rate'] = test_data.GR_rate
submission_data['GR'] = test_data.GR
submission_data['well_id'] = test_data.well_id
submission_data['row_id'] = test_data.row_id

In [83]:
for col in ['pred_2','pred_3','pred_4','pred_5','pred_6', 'pred_7', 'pred_8','pred_9','pred_10','pred_11','pred_12','pred_13','pred_14']:
    val_pred_df["{}_shift".format(col)] = val_pred_df.groupby('well_id')[col].shift(1)
    val_pred_df["{}_shift".format(col)] = val_pred_df["{}_shift".format(col)].fillna(method='bfill')
    
    submission_data["{}_shift".format(col)] = submission_data.groupby('well_id')[col].shift(1)
    submission_data["{}_shift".format(col)] = submission_data["{}_shift".format(col)].fillna(method='bfill')

In [84]:
for col in ['processed_GR','processed_GR2','GR_rate']:
    for shift in [11,22,55,110]:
        val_pred_df["rolling_{}_mean_{}".format(col,shift)] = val_pred_df[col].rolling(shift).mean()
        val_pred_df["rolling_{}_std_{}".format(col,shift)] = val_pred_df[col].rolling(shift).std()
        val_pred_df["rolling_{}_mean_{}".format(col,shift)] = val_pred_df["rolling_{}_mean_{}".format(col,shift)].fillna(method='bfill')
        val_pred_df["rolling_{}_std_{}".format(col,shift)] = val_pred_df["rolling_{}_std_{}".format(col,shift)].fillna(method='bfill')

In [85]:
for col in ['processed_GR','processed_GR2','GR_rate']:
    for shift in [11,22,55,110]:
        submission_data["rolling_{}_mean_{}".format(col,shift)] = submission_data[col].rolling(shift).mean()
        submission_data["rolling_{}_std_{}".format(col,shift)] = submission_data[col].rolling(shift).std()
        submission_data["rolling_{}_mean_{}".format(col,shift)] = submission_data["rolling_{}_mean_{}".format(col,shift)].fillna(method='bfill')
        submission_data["rolling_{}_std_{}".format(col,shift)] = submission_data["rolling_{}_std_{}".format(col,shift)].fillna(method='bfill')

In [86]:
list(val_pred_df.columns)

['row_id',
 'well_id',
 'GR',
 'label',
 'processed_GR',
 'processed_GR2',
 'GR_rate',
 'pred_2_0',
 'pred_2_1',
 'pred_2_2',
 'pred_2_3',
 'pred_2_4',
 'pred_2',
 'pred_3_0',
 'pred_3_1',
 'pred_3_2',
 'pred_3_3',
 'pred_3_4',
 'pred_3',
 'pred_4_0',
 'pred_4_1',
 'pred_4_2',
 'pred_4_3',
 'pred_4_4',
 'pred_4',
 'pred_5_0',
 'pred_5_1',
 'pred_5_2',
 'pred_5_3',
 'pred_5_4',
 'pred_5',
 'pred_6_0',
 'pred_6_1',
 'pred_6_2',
 'pred_6_3',
 'pred_6_4',
 'pred_6',
 'pred_7_0',
 'pred_7_1',
 'pred_7_2',
 'pred_7_3',
 'pred_7_4',
 'pred_7',
 'pred_8_0',
 'pred_8_1',
 'pred_8_2',
 'pred_8_3',
 'pred_8_4',
 'pred_8',
 'pred_9_0',
 'pred_9_1',
 'pred_9_2',
 'pred_9_3',
 'pred_9_4',
 'pred_9',
 'pred_10_0',
 'pred_10_1',
 'pred_10_2',
 'pred_10_3',
 'pred_10_4',
 'pred_10',
 'pred_11_0',
 'pred_11_1',
 'pred_11_2',
 'pred_11_3',
 'pred_11_4',
 'pred_11',
 'pred_12_0',
 'pred_12_1',
 'pred_12_2',
 'pred_12_3',
 'pred_12_4',
 'pred_12',
 'pred_13_0',
 'pred_13_1',
 'pred_13_2',
 'pred_13_3',
 'p

In [87]:
traincols = ['GR',
 'processed_GR',
 'processed_GR2',
 'GR_rate',
 'pred_2_0',
 'pred_2_1',
 'pred_2_2',
 'pred_2_3',
 'pred_2_4',
 'pred_2',
 'pred_3_0',
 'pred_3_1',
 'pred_3_2',
 'pred_3_3',
 'pred_3_4',
 'pred_3',
 'pred_4_0',
 'pred_4_1',
 'pred_4_2',
 'pred_4_3',
 'pred_4_4',
 'pred_4',
 'pred_5_0',
 'pred_5_1',
 'pred_5_2',
 'pred_5_3',
 'pred_5_4',
 'pred_5',
 'pred_6_0',
 'pred_6_1',
 'pred_6_2',
 'pred_6_3',
 'pred_6_4',
 'pred_6',
 'pred_7_0',
 'pred_7_1',
 'pred_7_2',
 'pred_7_3',
 'pred_7_4',
 'pred_7',
 'pred_8_0',
 'pred_8_1',
 'pred_8_2',
 'pred_8_3',
 'pred_8_4',
 'pred_8',
 'pred_9_0',
 'pred_9_1',
 'pred_9_2',
 'pred_9_3',
 'pred_9_4',
 'pred_9',
 'pred_10_0',
 'pred_10_1',
 'pred_10_2',
 'pred_10_3',
 'pred_10_4',
 'pred_10',
 'pred_11_0',
 'pred_11_1',
 'pred_11_2',
 'pred_11_3',
 'pred_11_4',
 'pred_11',
 'pred_12_0',
 'pred_12_1',
 'pred_12_2',
 'pred_12_3',
 'pred_12_4',
 'pred_12',
 'pred_13_0',
 'pred_13_1',
 'pred_13_2',
 'pred_13_3',
 'pred_13_4',
 'pred_13',
 'pred_14_0',
 'pred_14_1',
 'pred_14_2',
 'pred_14_3',
 'pred_14_4',
 'pred_14',
 'pred_2_shift',
 'pred_3_shift',
 'pred_4_shift',
 'pred_5_shift',
 'pred_6_shift',
 'pred_7_shift',
 'pred_8_shift',
 'pred_9_shift',
 'pred_10_shift',
 'pred_11_shift',
 'pred_12_shift',
 'pred_13_shift',
 'pred_14_shift',
 'rolling_processed_GR_mean_11',
 'rolling_processed_GR_std_11',
 'rolling_processed_GR_mean_22',
 'rolling_processed_GR_std_22',
 'rolling_processed_GR_mean_55',
 'rolling_processed_GR_std_55',
 'rolling_processed_GR_mean_110',
 'rolling_processed_GR_std_110',
 'rolling_processed_GR2_mean_11',
 'rolling_processed_GR2_std_11',
 'rolling_processed_GR2_mean_22',
 'rolling_processed_GR2_std_22',
 'rolling_processed_GR2_mean_55',
 'rolling_processed_GR2_std_55',
 'rolling_processed_GR2_mean_110',
 'rolling_processed_GR2_std_110',
 'rolling_GR_rate_mean_11',
 'rolling_GR_rate_std_11',
 'rolling_GR_rate_mean_22',
 'rolling_GR_rate_std_22',
 'rolling_GR_rate_mean_55',
 'rolling_GR_rate_std_55',
 'rolling_GR_rate_mean_110',
 'rolling_GR_rate_std_110']

In [88]:
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier
from sklearn.model_selection import cross_val_score

In [89]:
for i in range(2,15):
    print ("Val accuracy of model {} is {}".format(i,accuracy_score(val_pred_df.label,val_pred_df['pred_{}'.format(i)])))
    #print ("Val accuracy of shift model {} is {}".format(i,accuracy_score(val_pred_df.label,val_pred_df['pred_{}_shift'.format(i)])))

Val accuracy of model 2 is 0.9521670454545454
Val accuracy of model 3 is 0.9530272727272727
Val accuracy of model 4 is 0.9630431818181818
Val accuracy of model 5 is 0.9598386363636363
Val accuracy of model 6 is 0.9574045454545455
Val accuracy of model 7 is 0.6769477272727272
Val accuracy of model 8 is 0.9431840909090909
Val accuracy of model 9 is 0.9466284090909091
Val accuracy of model 10 is 0.9507465909090909
Val accuracy of model 11 is 0.9508806818181819
Val accuracy of model 12 is 0.9616397727272727
Val accuracy of model 13 is 0.9670409090909091
Val accuracy of model 14 is 0.9666784090909091


In [90]:
cross_val_score(X=val_pred_df[traincols],y=val_pred_df.label,cv=5,estimator=LogisticRegression(),groups=val_pred_df.well_id)

/Users/victor/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:433: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
/Users/victor/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:460: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)
/Users/victor/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:433: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
/Users/victor/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:460: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)
/Users/victor/anaconda3/lib/python3.7/site-packages/sklearn/linear_mod

array([0.96835813, 0.9682445 , 0.96514773, 0.96665322, 0.97127256])

In [91]:
np.mean([0.96835813, 0.9682445 , 0.96514773, 0.96665322, 0.97127256])

0.967935228

In [146]:
from sklearn import tree

In [147]:
dt = tree.DecisionTreeClassifier()
dt.fit(val_pred_df[traincols],val_pred_df.label)

DecisionTreeClassifier(class_weight=None, criterion='gini', max_depth=None,
            max_features=None, max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, presort=False, random_state=None,
            splitter='best')

In [156]:
val_pred_df.shape

(880000, 73)

In [216]:
dt2 = tree.DecisionTreeClassifier(max_depth=10)
dt2.fit(val_pred_df.iloc[:660000][traincols],val_pred_df.iloc[:660000].label)
accuracy_score(val_pred_df.iloc[660000:].label,dt2.predict(val_pred_df.iloc[660000:][traincols]))

0.9565454545454546

In [176]:
accuracy_score(val_pred_df.iloc[:660000].label,dt2.predict(val_pred_df.iloc[:660000][traincols]))

0.9682409090909091

In [159]:
from sklearn.naive_bayes import GaussianNB, MultinomialNB

In [177]:
?LogisticRegression

In [92]:
#nb = GaussianNB()
nb = LogisticRegression()
nb.fit(val_pred_df.iloc[:660000][traincols],val_pred_df.iloc[:660000].label)
accuracy_score(val_pred_df.iloc[660000:].label,nb.predict(val_pred_df.iloc[660000:][traincols]))

/Users/victor/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:433: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
/Users/victor/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:460: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)


0.9702409090909091

In [93]:
nb.coef_[0]

array([-2.37747323e-03,  1.62222493e-01,  1.90364422e-01, -7.44589882e-02,
        7.90593680e-01, -4.73565779e-01, -4.23072660e-01, -9.00958530e-01,
       -1.32672442e+00,  1.62440802e-01,  4.18582122e-01, -5.79050185e-01,
       -7.12914131e-01, -7.66623558e-01, -6.93722123e-01,  2.03601835e-01,
        1.85696642e+00, -8.64482832e-01, -1.03434266e+00, -8.29814462e-01,
       -1.46205445e+00,  2.98222513e-01,  2.28501445e-01, -8.46764925e-01,
       -1.14824239e+00, -5.46546432e-01, -2.06756246e-02,  1.73995862e-01,
       -7.26335541e-02, -3.71536471e-01, -5.51654141e-01, -5.41618166e-01,
       -7.96285844e-01,  1.33827666e-01,  1.94358091e-01, -1.23712178e-02,
       -2.51240538e+00,  7.80801783e-01, -7.84111085e-01, -8.45709019e-02,
       -5.64282719e-02,  3.18487009e-01, -8.51535311e-01, -8.03927850e-01,
       -9.40323059e-01,  1.36159812e-01,  1.29453987e-01, -1.35365751e-01,
       -3.65688128e-01, -1.52602460e+00, -4.36102753e-01,  9.80379565e-02,
       -1.17463508e+00, -

In [96]:
#nb.fit(val_pred_df[traincols],val_pred_df.label)
submission_ensemble = submission_data[['unique_id','label']].copy()
submission_ensemble['label'] = nb.predict(submission_data[traincols])
submission_ensemble.head(10)

unique_id  label
0     CAX_0      0
1     CAX_1      0
2     CAX_2      0
3     CAX_3      0
4     CAX_4      0
5     CAX_5      0
6     CAX_6      0
7     CAX_7      0
8     CAX_8      0
9     CAX_9      0

In [208]:
val_pred_df['max_label'] = val_pred_df[['pred_1','pred_2','pred_3','pred_4','pred_5','pred_6', 'pred_7', 'pred_8','pred_9','pred_10','pred_11']].mode(axis=1)




KeyboardInterrupt: 

In [203]:
val_pred_df[['pred_1','pred_2','pred_3','pred_4','pred_5','pred_6', 'pred_7', 'pred_8','pred_9','pred_10','pred_11']].max(axis=1).head()

0    0
1    0
2    0
3    0
4    0
dtype: int64

In [207]:
accuracy_score(val_pred_df.label,val_pred_df.max_label)

0.9589613636363636

In [97]:
submission_ensemble.to_csv('../data/submission14_ensemble.csv',index=False)

In [153]:
def print_decision_tree(tree, feature_names=None, offset_unit='    '):
    '''Plots textual representation of rules of a decision tree
    tree: scikit-learn representation of tree
    feature_names: list of feature names. They are set to f1,f2,f3,... if not specified
    offset_unit: a string of offset of the conditional block'''

    left      = tree.tree_.children_left
    right     = tree.tree_.children_right
    threshold = tree.tree_.threshold
    value = tree.tree_.value
    if feature_names is None:
        features  = ['f%d'%i for i in tree.tree_.feature]
    else:
        features  = [feature_names[i] for i in tree.tree_.feature]        

    def recurse(left, right, threshold, features, node, depth=0):
            offset = offset_unit*depth
            if (threshold[node] != -2):
                    print(offset+"if ( " + features[node] + " <= " + str(threshold[node]) + " ) {")
                    if left[node] != -1:
                            recurse (left, right, threshold, features,left[node],depth+1)
                    print(offset+"} else {")
                    if right[node] != -1:
                            recurse (left, right, threshold, features,right[node],depth+1)
                    print(offset+"}")
            else:
                    print(offset+"return " + str(value[node]))

    recurse(left, right, threshold, features, 0,0)

In [155]:
accuracy_score(val_pred_df.label,dt.predict(val_pred_df[traincols]))

1.0

In [154]:
print_decision_tree(dt,traincols)

if ( pred_4_0 <= 0.5233772099018097 ) {
    if ( pred_4_4 <= 0.4478372633457184 ) {
        if ( pred_4_2 <= 0.4538211226463318 ) {
            if ( pred_4_3 <= 0.3039254695177078 ) {
                if ( pred_4_1 <= 0.8839332461357117 ) {
                    if ( pred_5_0 <= 0.20386961102485657 ) {
                        if ( pred_6_2 <= 0.14233114570379257 ) {
                            if ( pred_5_3 <= 0.26921169459819794 ) {
                                if ( pred_6_4 <= 0.049533963203430176 ) {
                                    if ( pred_4_0 <= 1.5170796245911333e-06 ) {
                                        if ( pred_5_0 <= 2.761379505500372e-06 ) {
                                            return [[ 0.  0. 39.  0.  0.]]
                                        } else {
                                            if ( pred_3_0 <= 7.132932296372019e-05 ) {
                                                return [[ 0. 15.  0.  0.  0.]]
                                      

                                                                                    }
                                                                                } else {
                                                                                    return [[0. 0. 0. 2. 0.]]
                                                                                }
                                                                            } else {
                                                                                if ( pred_4_3 <= 0.08135317638516426 ) {
                                                                                    return [[0. 0. 1. 0. 0.]]
                                                                                } else {
                                                                                    return [[ 0. 29.  0.  0.  0.]]
                                                                                }
                               

                                                                        }
                                                                    }
                                                                } else {
                                                                    return [[0. 3. 0. 0. 0.]]
                                                                }
                                                            }
                                                        } else {
                                                            if ( pred_8_1 <= 0.28897346556186676 ) {
                                                                if ( pred_3_3 <= 0.8787994086742401 ) {
                                                                    if ( pred_1_1 <= 0.02785965148359537 ) {
                                                                        return [[0. 0. 0. 1. 0.]]
                                                                    } else {
       

                                                }
                                            } else {
                                                if ( pred_6_0 <= 0.0061444437596946955 ) {
                                                    if ( pred_2_0 <= 0.12136014923453331 ) {
                                                        if ( pred_3_3 <= 0.10287079587578773 ) {
                                                            if ( pred_2_0 <= 0.016459620790556073 ) {
                                                                return [[0. 5. 0. 0. 0.]]
                                                            } else {
                                                                return [[0. 0. 2. 0. 0.]]
                                                            }
                                                        } else {
                                                            if ( pred_1_3 <= 0.6666736602783203 ) {
                                      

                                                                    return [[0. 4. 0. 0. 0.]]
                                                                } else {
                                                                    return [[0. 0. 0. 1. 0.]]
                                                                }
                                                            } else {
                                                                return [[0. 0. 0. 8. 0.]]
                                                            }
                                                        }
                                                    } else {
                                                        if ( pred_5_1 <= 0.2408333495259285 ) {
                                                            if ( pred_4_4 <= 0.0004097555502085015 ) {
                                                                if ( pred_11_2 <= 0.0013892544811824337 ) {
                          

...

                                                                                                                        } else {
                                                                                                                            if ( pred_3_2 <= 0.00011620392251643352 ) {
                                                                                                                                return [[0. 1. 0. 0. 0.]]
                                                                                                                            } else {
                                                                                                                                return [[1. 0. 0. 0. 0.]]
                                                                                                                            }
                                                                                                                        }
              

                                                                                                                        return [[0. 0. 0. 1. 0.]]
                                                                                                                    } else {
                                                                                                                        return [[4. 0. 0. 0. 0.]]
                                                                                                                    }
                                                                                                                } else {
                                                                                                                    if ( pred_6_1 <= 0.001263428304810077 ) {
                                                                                                                        if ( pred_9_4 <= 0.005835391115397215 ) {
                        

                                                                                    }
                                                                                } else {
                                                                                    if ( pred_6_4 <= 0.013272557873278856 ) {
                                                                                        if ( pred_6_4 <= 0.013256094418466091 ) {
                                                                                            if ( pred_3_2 <= 8.310620614793152e-05 ) {
                                                                                                return [[65.  0.  0.  0.  0.]]
                                                                                            } else {
                                                                                                if ( pred_7_2 <= 0.0020707903895527124 ) {
                                                                   

                                                                                                    } else {
                                                                                                        if ( pred_8_2 <= 0.0002646654102136381 ) {
                                                                                                            return [[0. 0. 0. 0. 1.]]
                                                                                                        } else {
                                                                                                            return [[4. 0. 0. 0. 0.]]
                                                                                                        }
                                                                                                    }
                                                                                                }
                                                         

                                                                                } else {
                                                                                    return [[0. 0. 0. 1. 0.]]
                                                                                }
                                                                            }
                                                                        } else {
                                                                            if ( pred_4_2 <= 9.571057944413042e-06 ) {
                                                                                if ( pred_9_1 <= 0.00025217993243131787 ) {
                                                                                    if ( pred_9_1 <= 0.0002519727568142116 ) {
                                                                                        if ( pred_7_4 <= 0.00835098186507821 ) {
                                                             

In [151]:
import graphviz 
dot_data = tree.export_graphviz(dt, out_file=None, 
                      feature_names=traincols,  
                      filled=True, rounded=True,  
                      special_characters=True)  
graph = graphviz.Source(dot_data)  
graph 

KeyboardInterrupt: 

In [112]:
cross_val_score(X=val_pred_df[traincols],y=val_pred_df.label,cv=5,estimator=RandomForestClassifier(n_estimators=100,random_state=123),groups=val_pred_df.well_id)



array([0.96556838, 0.96559679, 0.96108523, 0.96296002, 0.96761913])

In [113]:
np.mean([0.96556838, 0.96559679, 0.96108523, 0.96296002, 0.96761913])

0.9645659099999999

In [122]:
cross_val_score(X=val_pred_df[traincols],y=val_pred_df.label,cv=5,estimator=GradientBoostingClassifier(learning_rate=.1,n_estimators=100,random_state=123),groups=val_pred_df.well_id)


array([0.96582406, 0.96534111, 0.96124432, 0.96254524, 0.96812482])

In [124]:
np.mean([0.96582406, 0.96534111, 0.96124432, 0.96254524, 0.96812482])

0.96461591

In [99]:
import xgboost as xgb
import lightgbm as lgb

/Users/victor/anaconda3/lib/python3.7/site-packages/lightgbm/__init__.py:46: UserWarning: Starting from version 2.2.1, the library file in distribution wheels for macOS is built by the Apple Clang (Xcode_8.3.3) compiler.
This means that in case of installing LightGBM from PyPI via the ``pip install lightgbm`` command, you don't need to install the gcc compiler anymore.
Instead of that, you need to install the OpenMP library, which is required for running LightGBM on the system with the Apple Clang compiler.
You can install the OpenMP library by the following command: ``brew install libomp``.
  "You can install the OpenMP library by the following command: ``brew install libomp``.", UserWarning)


In [100]:
clf = xgb.XGBClassifier(max_depth=31,n_estimators=200,objective='multi:softprob')

In [130]:
cross_val_score(X=val_pred_df[traincols],y=val_pred_df.label,cv=5,estimator=clf,groups=val_pred_df.well_id)


array([0.96547179, 0.96502293, 0.96113636, 0.96219865, 0.96681799])

In [131]:
np.mean([0.96547179, 0.96502293, 0.96113636, 0.96219865, 0.96681799])

0.9641295440000001

In [101]:
#nb = GaussianNB()
#nb = LogisticRegression()
clf.fit(val_pred_df.iloc[:660000][traincols],val_pred_df.iloc[:660000].label)
accuracy_score(val_pred_df.iloc[660000:].label,clf.predict(val_pred_df.iloc[660000:][traincols]))

KeyboardInterrupt: 

In [147]:
traincols2 = [
 'processed_GR2',
 'GR_rate',
 'pred_2_0',
 'pred_2_1',
 'pred_2_2',
 'pred_2_3',
 'pred_2_4',
 'pred_3_0',
 'pred_3_1',
 'pred_3_2',
 'pred_3_3',
 'pred_3_4',
 'pred_4_0',
 'pred_4_1',
 'pred_4_2',
 'pred_4_3',
 'pred_4_4',
 'pred_5_0',
 'pred_5_1',
 'pred_5_2',
 'pred_5_3',
 'pred_5_4',
 'pred_6_0',
 'pred_6_1',
 'pred_6_2',
 'pred_6_3',
 'pred_6_4',
 'pred_7_0',
 'pred_7_1',
 'pred_7_2',
 'pred_7_3',
 'pred_7_4',
 'pred_8_0',
 'pred_8_1',
 'pred_8_2',
 'pred_8_3',
 'pred_8_4',
 'pred_9_0',
 'pred_9_1',
 'pred_9_2',
 'pred_9_3',
 'pred_9_4',
 'pred_10_0',
 'pred_10_1',
 'pred_10_2',
 'pred_10_3',
 'pred_10_4',
 'pred_11_0',
 'pred_11_1',
 'pred_11_2',
 'pred_11_3',
 'pred_11_4',
 'pred_12_0',
 'pred_12_1',
 'pred_12_2',
 'pred_12_3',
 'pred_12_4',
 'pred_13_0',
 'pred_13_1',
 'pred_13_2',
 'pred_13_3',
 'pred_13_4',
 'pred_14_0',
 'pred_14_1',
 'pred_14_2',
 'pred_14_3',
 'pred_14_4']

In [154]:
def get_simple_ensemble_model():
    model = Sequential()
    model.add(InputLayer(input_shape=(max_len,len(traincols2))))
    model.add(Bidirectional(LSTM(100, dropout=0.2, recurrent_dropout=0.2, return_sequences = True)))
    model.add(Dense(200,activation='relu'))
    model.add(Dense(200,activation='relu'))
    model.add(Dense(200,activation='relu'))
    #model.add(SeqSelfAttention(attention_width=50,attention_activation='sigmoid',name='Attention'))
    model.add(Dense(n_output,activation='softmax'))
    model.compile(loss = 'categorical_crossentropy', optimizer="nadam",metrics = ['accuracy'])
    #print(model.summary())
    return model

In [152]:
model = get_simple_ensemble_model()
model.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
bidirectional_77 (Bidirectio (None, 1100, 200)         134400    
_________________________________________________________________
dense_95 (Dense)             (None, 1100, 200)         40200     
_________________________________________________________________
dense_96 (Dense)             (None, 1100, 200)         40200     
_________________________________________________________________
dense_97 (Dense)             (None, 1100, 200)         40200     
_________________________________________________________________
dense_98 (Dense)             (None, 1100, 5)           1005      
Total params: 256,005
Trainable params: 256,005
Non-trainable params: 0
_________________________________________________________________


In [123]:
val_pred_df.label.value_counts(normalize=True)

0    0.524042
4    0.122483
3    0.119023
2    0.118386
1    0.116066
Name: label, dtype: float64

In [157]:
from keras.optimizers import Adam, Nadam

In [148]:
val_pred_df_x = val_pred_df[traincols2].values.reshape(val_pred_df.well_id.nunique(),max_len,len(traincols2))
val_pred_df_y = pd.get_dummies(val_pred_df.label).values.reshape(val_pred_df.well_id.nunique(),max_len,5)

print (val_pred_df_x.shape, val_pred_df_y.shape)

(800, 1100, 67) (800, 1100, 5)


In [120]:
def focal_loss(gamma=2., alpha=4.):

    gamma = float(gamma)
    alpha = float(alpha)

    def focal_loss_fixed(y_true, y_pred):
        """Focal loss for multi-classification
        FL(p_t)=-alpha(1-p_t)^{gamma}ln(p_t)
        Notice: y_pred is probability after softmax
        gradient is d(Fl)/d(p_t) not d(Fl)/d(x) as described in paper
        d(Fl)/d(p_t) * [p_t(1-p_t)] = d(Fl)/d(x)
        Focal Loss for Dense Object Detection
        https://arxiv.org/abs/1708.02002

        Arguments:
            y_true {tensor} -- ground truth labels, shape of [batch_size, num_cls]
            y_pred {tensor} -- model's output, shape of [batch_size, num_cls]

        Keyword Arguments:
            gamma {float} -- (default: {2.0})
            alpha {float} -- (default: {4.0})

        Returns:
            [tensor] -- loss.
        """
        epsilon = 1.e-9
        y_true = tf.convert_to_tensor(y_true, tf.float32)
        y_pred = tf.convert_to_tensor(y_pred, tf.float32)

        model_out = tf.add(y_pred, epsilon)
        ce = tf.multiply(y_true, -tf.log(model_out))
        weight = tf.multiply(y_true, tf.pow(tf.subtract(1., model_out), gamma))
        fl = tf.multiply(alpha, tf.multiply(weight, ce))
        reduced_fl = tf.reduce_max(fl, axis=1)
        return tf.reduce_mean(reduced_fl)
    return focal_loss_fixed

In [119]:
iter = 0
n_epochs = 50
all_history = {}

for train_index, test_index in KFold(n_splits=5).split(val_pred_df_x,val_pred_df_y):
    iter += 1
    
    print ("Iteration {}".format(iter))
    
    train_x = val_pred_df_x[train_index]
    train_y = val_pred_df_y[train_index]
    val_x = val_pred_df_x[test_index]
    val_y = val_pred_df_y[test_index]
    
    #print (train_x.shape, train_y.shape, val_x.shape, val_y.shape)
    model = get_simple_ensemble_model()
    
    #model.load_weights("weights1.hdf5")
    early = EarlyStopping(monitor='val_acc', min_delta=0, patience=10, verbose=0, mode='max', baseline=None, restore_best_weights=False)
    lr = ReduceLROnPlateau(monitor='val_loss', factor=0.1, patience=5, verbose=0, mode='auto', min_delta=0.0001, cooldown=0, min_lr=0.000001)
    checkpointer = ModelCheckpoint(monitor='val_acc',filepath='../working/weights_lstm_ensemble_fl_{}.hdf5'.format(iter), mode='max',verbose=1, save_best_only=True)
    
    history = model.fit(train_x, train_y, epochs = n_epochs, batch_size=batch_size, verbose = 1, validation_data=(val_x,val_y), callbacks=[early,lr,checkpointer])
    all_history[iter] = history
    
    break

Iteration 1
Train on 640 samples, validate on 160 samples
Epoch 1/50
640/640 [==============================] - 37s 59ms/step - loss: 0.8523 - acc: 0.7371 - val_loss: 0.3193 - val_acc: 0.9278

Epoch 00001: val_acc improved from -inf to 0.92776, saving model to ../working/weights_lstm_ensemble_1.hdf5
Epoch 2/50
640/640 [==============================] - 24s 37ms/step - loss: 0.2297 - acc: 0.9491 - val_loss: 0.1739 - val_acc: 0.9569

Epoch 00002: val_acc improved from 0.92776 to 0.95687, saving model to ../working/weights_lstm_ensemble_1.hdf5
Epoch 3/50
640/640 [==============================] - 25s 39ms/step - loss: 0.1643 - acc: 0.9574 - val_loss: 0.1487 - val_acc: 0.9614

Epoch 00003: val_acc improved from 0.95687 to 0.96145, saving model to ../working/weights_lstm_ensemble_1.hdf5
Epoch 4/50
640/640 [==============================] - 26s 40ms/step - loss: 0.1463 - acc: 0.9611 - val_loss: 0.1388 - val_acc: 0.9631

Epoch 00004: val_acc improved from 0.96145 to 0.96313, saving model to .

640/640 [==============================] - 24s 38ms/step - loss: 0.0990 - acc: 0.9684 - val_loss: 0.1020 - val_acc: 0.9689

Epoch 00037: val_acc improved from 0.96881 to 0.96889, saving model to ../working/weights_lstm_ensemble_1.hdf5
Epoch 38/50
640/640 [==============================] - 24s 38ms/step - loss: 0.0983 - acc: 0.9683 - val_loss: 0.1016 - val_acc: 0.9688

Epoch 00038: val_acc did not improve from 0.96889
Epoch 39/50
640/640 [==============================] - 24s 38ms/step - loss: 0.0975 - acc: 0.9683 - val_loss: 0.1019 - val_acc: 0.9683

Epoch 00039: val_acc did not improve from 0.96889
Epoch 40/50
640/640 [==============================] - 24s 38ms/step - loss: 0.0980 - acc: 0.9684 - val_loss: 0.1025 - val_acc: 0.9683

Epoch 00040: val_acc did not improve from 0.96889
Epoch 41/50
640/640 [==============================] - 24s 38ms/step - loss: 0.0974 - acc: 0.9687 - val_loss: 0.1022 - val_acc: 0.9689

Epoch 00041: val_acc improved from 0.96889 to 0.96893, saving model to 

In [139]:
iter = 0
n_epochs = 100
all_history = {}

for train_index, test_index in KFold(n_splits=5).split(val_pred_df_x,val_pred_df_y):
    iter += 1
    
    print ("Iteration {}".format(iter))
    
    train_x = val_pred_df_x[train_index]
    train_y = val_pred_df_y[train_index]
    val_x = val_pred_df_x[test_index]
    val_y = val_pred_df_y[test_index]
    
    #print (train_x.shape, train_y.shape, val_x.shape, val_y.shape)
    model = get_simple_ensemble_model()
    model.compile(loss='categorical_crossentropy',
              optimizer='nadam',
              metrics=['accuracy'])
    class_weight = {0:1,1:5,2:5,3:4,4:5}
    #model.load_weights("weights1.hdf5")
    early = EarlyStopping(monitor='val_acc', min_delta=0, patience=10, verbose=0, mode='max', baseline=None, restore_best_weights=False)
    lr = ReduceLROnPlateau(monitor='val_loss', factor=0.1, patience=5, verbose=0, mode='auto', min_delta=0.0001, cooldown=0, min_lr=0.000001)
    checkpointer = ModelCheckpoint(monitor='val_acc',filepath='../working/weights_lstm_ensemble_fl_{}.hdf5'.format(iter), mode='max',verbose=1, save_best_only=True)
    
    history = model.fit(train_x, train_y, epochs = n_epochs, batch_size=batch_size, verbose = 1, validation_data=(val_x,val_y), callbacks=[early,lr,checkpointer])
    all_history[iter] = history
    
    break

Iteration 1
Train on 640 samples, validate on 160 samples
Epoch 1/100
640/640 [==============================] - 15s 24ms/step - loss: 0.3253 - acc: 0.9371 - val_loss: 0.1241 - val_acc: 0.9665

Epoch 00001: val_acc improved from -inf to 0.96650, saving model to ../working/weights_lstm_ensemble_fl_1.hdf5
Epoch 2/100
640/640 [==============================] - 5s 8ms/step - loss: 0.1192 - acc: 0.9671 - val_loss: 0.1145 - val_acc: 0.9677

Epoch 00002: val_acc improved from 0.96650 to 0.96774, saving model to ../working/weights_lstm_ensemble_fl_1.hdf5
Epoch 3/100
640/640 [==============================] - 5s 8ms/step - loss: 0.1108 - acc: 0.9681 - val_loss: 0.1130 - val_acc: 0.9675

Epoch 00003: val_acc did not improve from 0.96774
Epoch 4/100
640/640 [==============================] - 5s 8ms/step - loss: 0.1068 - acc: 0.9682 - val_loss: 0.1088 - val_acc: 0.9675

Epoch 00004: val_acc did not improve from 0.96774
Epoch 5/100
640/640 [==============================] - 5s 8ms/step - loss: 0.10

In [159]:
def weighted_categorical_crossentropy(weights):
    """
    A weighted version of keras.objectives.categorical_crossentropy
    
    Variables:
        weights: numpy array of shape (C,) where C is the number of classes
    
    Usage:
        weights = np.array([0.5,2,10]) # Class one at 0.5, class 2 twice the normal weights, class 3 10x.
        loss = weighted_categorical_crossentropy(weights)
        model.compile(loss=loss,optimizer='adam')
    """
    
    weights = K.variable(weights)
        
    def loss(y_true, y_pred):
        # scale predictions so that the class probas of each sample sum to 1
        y_pred /= K.sum(y_pred, axis=-1, keepdims=True)
        # clip to prevent NaN's and Inf's
        y_pred = K.clip(y_pred, K.epsilon(), 1 - K.epsilon())
        # calc
        loss = y_true * K.log(y_pred) * weights
        loss = -K.sum(loss, -1)
        return loss
    
    return loss

In [160]:
from sklearn.utils import class_weight
class_weights = class_weight.compute_class_weight('balanced',
                                                 np.unique(train_data.label),
                                                 train_data.label)
class_weights

array([0.38041206, 1.68988985, 1.67499086, 1.68537174, 1.69733769])

In [163]:
iter = 0
n_epochs = 100
all_history = {}

for train_index, test_index in KFold(n_splits=5).split(val_pred_df_x,val_pred_df_y):
    iter += 1
    
    print ("Iteration {}".format(iter))
    
    train_x = val_pred_df_x[train_index]
    train_y = val_pred_df_y[train_index]
    val_x = val_pred_df_x[test_index]
    val_y = val_pred_df_y[test_index]
    
    #print (train_x.shape, train_y.shape, val_x.shape, val_y.shape)
    model = get_simple_ensemble_model()
    #model.compile(loss=weighted_categorical_crossentropy(class_weights),
    #          optimizer="nadam",
    #          metrics=['accuracy'])
    #model.load_weights("weights1.hdf5")
    early = EarlyStopping(monitor='val_acc', min_delta=0, patience=10, verbose=0, mode='max', baseline=None, restore_best_weights=False)
    lr = ReduceLROnPlateau(monitor='val_loss', factor=0.1, patience=5, verbose=0, mode='auto', min_delta=0.0001, cooldown=0, min_lr=0.000001)
    checkpointer = ModelCheckpoint(monitor='val_acc',filepath='../working/weights_lstm_ensemble_fl2_{}.hdf5'.format(iter), mode='max',verbose=1, save_best_only=True)
    
    history = model.fit(train_x, train_y, epochs = n_epochs, batch_size=batch_size, verbose = 1, validation_data=(val_x,val_y), callbacks=[early,lr,checkpointer])
    all_history[iter] = history
    
    break

Iteration 1
Train on 640 samples, validate on 160 samples
Epoch 1/100
640/640 [==============================] - 29s 46ms/step - loss: 0.0898 - acc: 0.9695 - val_loss: 0.0977 - val_acc: 0.9688

Epoch 00001: val_acc improved from -inf to 0.96884, saving model to ../working/weights_lstm_ensemble_fl2_1.hdf5
Epoch 2/100
640/640 [==============================] - 28s 44ms/step - loss: 0.0891 - acc: 0.9696 - val_loss: 0.0976 - val_acc: 0.9689

Epoch 00002: val_acc improved from 0.96884 to 0.96890, saving model to ../working/weights_lstm_ensemble_fl2_1.hdf5
Epoch 3/100
640/640 [==============================] - 28s 44ms/step - loss: 0.0888 - acc: 0.9699 - val_loss: 0.0976 - val_acc: 0.9689

Epoch 00003: val_acc improved from 0.96890 to 0.96893, saving model to ../working/weights_lstm_ensemble_fl2_1.hdf5
Epoch 4/100
640/640 [==============================] - 28s 44ms/step - loss: 0.0890 - acc: 0.9698 - val_loss: 0.0976 - val_acc: 0.9689

Epoch 00004: val_acc improved from 0.96893 to 0.96893, s

KeyboardInterrupt: 

In [142]:
submission_ensemble = submission_data[['unique_id','label']].copy()
test_pred = model.predict(submission_data[traincols2].values.reshape(submission_data.well_id.nunique(),1100,len(traincols2))).argmax(axis=-1)

In [143]:
test_pred.shape

(2000, 1100)

In [144]:
submission_ensemble['label'] = test_pred.reshape(submission_data.well_id.nunique()*1100)
submission_ensemble.head(10)

unique_id  label
0     CAX_0      0
1     CAX_1      0
2     CAX_2      0
3     CAX_3      0
4     CAX_4      0
5     CAX_5      0
6     CAX_6      0
7     CAX_7      0
8     CAX_8      0
9     CAX_9      0

In [146]:
submission_ensemble.to_csv("../data/submission_model15_dense_ensemble.csv",index=False)

In [164]:
submission_ensemble.label.value_counts(normalize=True)

0    0.528775
1    0.120071
4    0.119475
2    0.117946
3    0.113733
Name: label, dtype: float64